In [1]:
#!/usr/bin/python
# -*- coding: utf-8 -*-
# ========== python ==========
import os
from pathlib import Path
from logging import Logger
from typing import List, Dict, Tuple, Optional, Union, Callable, Final, Literal, get_args
from operator import itemgetter, attrgetter
import itertools
from IPython.display import display

from utils.setup import setup_logger, get_device
from const.const_values import PROJECT_DIR

os.chdir(PROJECT_DIR)
logger: Logger = setup_logger(__name__, f'{PROJECT_DIR}/log/jupyter_run.log')
device = get_device(device_name='cpu', logger=logger)

In [2]:
# jupyter
import seaborn as sns
import matplotlib.pyplot as plt
# Machine learning
import numpy as np
import pandas as pd
import h5py
import optuna
# torch
import torch
from torch.nn import CrossEntropyLoss
from torch.utils.data import Dataset
from torch.utils.data.dataloader import DataLoader
from torch.utils.tensorboard.writer import SummaryWriter
# torch ignite
from ignite.engine import Engine
from ignite.handlers import Checkpoint
# My items
from models.datasets.data_helper import MyDataHelper, MyDataLoaderHelper, DefaultTokens
from models.datasets.datasets_for_story import StoryTriple
# My utils
from utils.setup import load_param
from utils.torch import load_model, torch_fix_seed
# main function
from run_for_KGC import main_function

In [3]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 100)

In [4]:
from const.const_values import CPU, MODEL
from models.KGModel.kg_model import HEAD, RELATION, TAIL
from utils.torch_ignite import TRAINER, EVALUATOR
from const.const_values import DATASETS, DATA_HELPER, DATA_LOADERS, TRAIN_RETURNS

In [5]:
SEED: Final[int] = 42
args_path = f'{PROJECT_DIR}/models/kgc03a/all100/param.pkl'
model_path = f'{PROJECT_DIR}/models/kgc03a/all100/model.pth'

In [6]:
args = load_param(args_path)

# args.pre_train = True
args.logger = logger
args.device = device
args.batch_size = 1
args.pre_train=False
args.init_embedding_using_bert = False
args.model_path = model_path
args.only_load_trainer_evaluator = True
args.old_data = 1

del args.optuna_file, args.device_name, args.pid, args.study_name, args.n_trials

### ↑ import and setting const value complete.  ↑

In [7]:
args

Namespace(notebook=False, console_level='info', logfile='models/kgc/all100/03/log.log', param_file='models/kgc/all100/03/param.pkl', train_anyway=False, tensorboard_dir='models/kgc/all100/03/tensorboard', checkpoint_dir='models/kgc/all100/03/checkpoint/', model_path='/Users/ryoyakaneda/Documents/学校/M1Study/knowledge_graph/models/kgc03a/all100/model.pth', resume_from_checkpoint=False, resume_from_last_point=False, only_load_trainer_evaluator=True, resume_checkpoint_path=None, pre_train=False, train_valid_test=False, only_train=True, use_for_challenge100=False, use_for_challenge090=False, use_for_challenge075=False, use_title=None, do_optuna=False, story_special_num=5, relation_special_num=5, entity_special_num=5, padding_token_e=0, cls_token_e=1, mask_token_e=2, sep_token_e=3, bos_token_e=4, padding_token_r=0, cls_token_r=1, mask_token_r=2, sep_token_r=3, bos_token_r=4, padding_token_s=0, cls_token_s=1, mask_token_s=2, sep_token_s=3, bos_token_s=4, model_version='03', embedding_dim=128,

These are the parameters related to the model.

In [26]:
"embedding_dim={}, entity_embedding_dim={}, relation_embedding_dim={}, nhead={}, num_layers={}, ".format(
    args.embedding_dim, args.entity_embedding_dim, args.relation_embedding_dim, args.nhead, args.num_layers,)

'embedding_dim=128, entity_embedding_dim=128, relation_embedding_dim=64, nhead=4, num_layers=4, '

First, the model is initialized and then overwritten with a previously saved model.

At this time, training data and so on are obtained at the same time.

In [27]:
torch_fix_seed(seed=SEED)
return_dict = main_function(args, logger=logger)

2023-02-03 05:31:18 - INFO - run_for_KGC.py - 892 - ----- make datahelper start. -----
2023-02-03 05:31:18 - INFO - run_for_KGC.py - 587 - ----- use old data (version 1) -----
2023-02-03 05:31:18 - INFO - data_helper.py - 333 - ====== Show MyRawData ======
2023-02-03 05:31:18 - INFO - data_helper.py - 334 - entity num: 7844
2023-02-03 05:31:18 - INFO - data_helper.py - 335 - relation num: 63
2023-02-03 05:31:18 - INFO - data_helper.py - 336 - ====== Show MyRawData ======
2023-02-03 05:31:18 - INFO - data_helper.py - 607 - ========== Show DataHelper ==========
2023-02-03 05:31:18 - INFO - data_helper.py - 333 - ====== Show MyRawData ======
2023-02-03 05:31:18 - INFO - data_helper.py - 334 - entity num: 7844
2023-02-03 05:31:18 - INFO - data_helper.py - 335 - relation num: 63
2023-02-03 05:31:18 - INFO - data_helper.py - 336 - ====== Show MyRawData ======
2023-02-03 05:31:18 - INFO - data_helper.py - 609 - entity_special_dicts: {0: '<pad_e>', 1: '<cls_e>', 2: '<mask_e>', 3: '<sep_e>', 4:

In [9]:
model = return_dict[MODEL]

dataset_train: StoryTriple = return_dict[DATASETS][0]
triple: torch.Tensor = dataset_train.triple
data_helper: MyDataHelper = return_dict[DATA_HELPER]
evaluator: Checkpoint = return_dict[TRAIN_RETURNS][EVALUATOR]

load_model(model, args.model_path, device)
model.eval()

entities, relations = data_helper.processed_entities, data_helper.processed_relations
d_e, d_r = {e: i for i, e in enumerate(entities)}, {r: i for i, r in enumerate(relations)}

triple_df = pd.DataFrame([(entities[_t[0]], relations[_t[1]], entities[_t[2]]) for _t in triple], columns=[HEAD, RELATION, TAIL])
story_entities = triple_df[HEAD].tolist()

One of the inputs is shown as an example.

The sequence contains triples from the beginning of each scene to the specified length. In this case, the length is set to 512.

In [28]:
print("training sequence shape:", dataset_train[0].shape)
dataset_train[0],

training sequence shape: torch.Size([512, 3])


(tensor([[   4,    4,    4],
         [3960,   38,   26],
         [3960,   21, 7238],
         ...,
         [4048,   45,  549],
         [   4,    4,    4],
         [4049,   38,   32]]),)

Note that the data presented in the previous section are part of this series.

In [11]:
triple_df

head          relation  \
0              <bos_e>           <bos_r>   
1      AbbeyGrange:001       kgc:subject   
2      AbbeyGrange:001  kgc:hasPredicate   
3      AbbeyGrange:001          kgc:whom   
4      AbbeyGrange:001    kgc:infoSource   
...                ...               ...   
17886  AbbeyGrange:084       kgc:subject   
17887  AbbeyGrange:084  kgc:hasPredicate   
17888  AbbeyGrange:084         kgc:where   
17889          <bos_e>           <bos_r>   
17890  AbbeyGrange:085       kgc:subject   

                                        tail  
0                                    <bos_e>  
1                            AllTitle:Holmes  
2                      word.predicate:wakeUp  
3                            AllTitle:Watson  
4                            AllTitle:Watson  
...                                      ...  
17886                    AbbeyGrange:Theresa  
17887                    word.predicate:rest  
17888  AbbeyGrange:room_of_Lady_Brackenstall  
17889                                <bos_e>  
17890          AbbeyGrange:Lady_Brackenstall  

[17891 rows x 3 columns]

This is the model made by Pytorch.

In [29]:
model

KgStoryTransformer03(
  (entity_embeddings): Embedding(7849, 128, padding_idx=0)
  (relation_embeddings): Embedding(68, 64, padding_idx=0)
  (pe): PositionalEncoding(
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (transformer): TransformerEncoder(
    (layers): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiheadAttention(
          (out_proj): NonDynamicallyQuantizableLinear(in_features=128, out_features=128, bias=True)
        )
        (linear1): Linear(in_features=128, out_features=1028, bias=True)
        (dropout): Dropout(p=0.1, inplace=False)
        (linear2): Linear(in_features=1028, out_features=128, bias=True)
        (norm1): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (norm2): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (dropout1): Dropout(p=0.1, inplace=False)
        (dropout2): Dropout(p=0.1, inplace=False)
        (activation): GELU(approximate='none')
      )
      (1): TransformerEncoderLayer(
      

This function is used to visualize Attention. The description is skipped.

In [13]:
# This is sub functions for getting Attention.
def extract(_model, target, inputs):
    """This is sub functions for getting Attention.

    """
    features = None

    def forward_hook(_module, _inputs, _):
        nonlocal features
        x, _, _ = _inputs
        outputs = _module.forward(x, x, x, need_weights=True)[1]
        features = outputs.detach().clone()

    handle = target.register_forward_hook(forward_hook)

    _model.eval()
    _model(inputs, torch.LongTensor([[]]), torch.LongTensor([[]]), torch.LongTensor([[]]))

    handle.remove()

    return features

# This is main functions for getting Attention.
def get_attention(input_):
    """This is main functions for getting Attention.

    """
    assert len(input_) == 1
    features = extract(model, model.transformer.layers[-1].self_attn, input_)[0]
    df_attention = pd.DataFrame([[entities[h], relations[r], entities[t]]+[features[j, i].item() for j in range(len(features))] for i, (h, r, t) in enumerate(input_[0])])
    df_attention.columns=[HEAD, RELATION, TAIL] + [f'atten_from{i}' for i in range(len(df_attention.columns)-3)]
    return df_attention

def show_attention_heatmap(df_attention):
    sns.heatmap(df_attention.iloc[:,3:])
    plt.show()

In [14]:
MASK_E = DefaultTokens.MASK_E
KILL = 'word.predicate:kill'

TAKE = 'word.predicate:take'
BRING = 'word.predicate:bring'
DIE = 'word.predicate:die'
HIDE = 'word.predicate:hide'

The input to the model is the following function's "question_".
There are some last scenes and criminal scene after last scene.
Each part of criminal scene are changed into a victim or <mask>, and the MASK part is estimated.

In [15]:
bos_triple = [d_e[DefaultTokens.BOS_E], d_r[DefaultTokens.BOS_R],d_e[DefaultTokens.BOS_E]]
mask_e_id = d_e[DefaultTokens.MASK_E]
Holmes_id =d_e['AllTitle:Holmes']

def make_ranking(from_story_name, to_story_name, predicate_, whom_, subject_, why_, what_, where_):
    if not (from_story_name is None and to_story_name is None):
        _start_index = story_entities.index(from_story_name)-1
        _end_index = len(story_entities) - story_entities[::-1].index(to_story_name)
    else:
        _start_index = 0
        _end_index = 0
    question_ = torch.tensor(
        [
            bos_triple,
            [mask_e_id, d_r['kgc:infoSource'],     Holmes_id      ],
            [mask_e_id, d_r['kgc:hasPredicate'],   d_e[predicate_]],
            [mask_e_id, d_r['kgc:whom'],           d_e[whom_     ]],
            [mask_e_id, d_r['kgc:subject'],        d_e[subject_  ]],
            [mask_e_id, d_r['kgc:why'],            d_e[why_      ]],
            [mask_e_id, d_r['kgc:what'],           d_e[what_     ]],
            [mask_e_id, d_r['kgc:where'],          d_e[where_    ]],
        ]
    )
    mask_ = torch.zeros_like(question_, dtype=torch.bool) # not mask all position
    mask_[1:, 0] = True                                   # where head position without bos token
    mask_[1:, 2] = True                                   # where tail position without bos token

    last_triples = triple[_start_index: _end_index]

    questions = torch.cat([last_triples, question_], dim=0).unsqueeze(0)
    masks = torch.cat([torch.zeros_like(last_triples), mask_], dim=0).to(torch.bool).transpose(1,0).unsqueeze(0)

    data_list = []
    with torch.no_grad():
        _, (story_pred, relation_pred, entity_pred) = model(questions, masks[:,0], masks[:,1], masks[:,2])
        sorted_ = torch.argsort(entity_pred, dim=1, descending=True)
        for i in range(sorted_.shape[1]):
            ans_= sorted_[:, i]
            info_source_, predicate_pred, whom_pred, subject_pred, why_pred, what_pred, where_pred = ans_
            data_list.append([entities[predicate_pred], entities[whom_pred], entities[subject_pred], entities[why_pred], entities[what_pred], entities[where_pred]])
    df_ranking = pd.DataFrame(data_list, columns=['predicate', 'whom', 'subject', 'why', 'what', 'where'])
    df_attension = get_attention(questions)

    return df_ranking, df_attension

In [16]:
def main_func01(_title, _victim_name, criminal, predicate, _last_index, _story_len):
    from_ = f'{_title}:{_last_index-_story_len+1}'
    to_ = f'{_title}:{_last_index}'
    predicate = predicate
    victim = f'{_title}:{_victim_name}'
    criminal = f'{_title}:{criminal}'
    df_ranking, df_attension = make_ranking(
        from_, to_, predicate, victim, MASK_E, MASK_E, MASK_E, MASK_E)

    pred_rank = df_ranking.index[df_ranking['subject']==criminal].tolist()
    pred_rank = pred_rank[0] if len(pred_rank)==1 else -1
    logger.info(f"The pred ranking about {criminal} is {pred_rank}")
    display(df_ranking.iloc[:max(20, pred_rank)])
    len_ = len(df_attension)
    for i in range(len_-10, len_):
        print(f"index={i}, triple={df_attension.iloc[i,:3].tolist()}, attention list")
        display(df_attension.sort_values(f'atten_from{i}', ascending=False).iloc[:,[0,1,2,3+i]],)
    return df_ranking, df_attension

def check_killer(_title, _victim_name, _killer_name, _last_index, _story_len):
    return main_func01(_title, _victim_name, _killer_name, KILL, _last_index, _story_len)

# Estimate Criminals

### SpeckledBand(まだらの紐)
Who killed Julia? (criminal & explanation)
被害者: Julia
犯人: Roylott
犯行に用いたもの: snake
犯行動機: 母の相続財産を独占したい

Input sequence is like this.


|     head     | relation  |            tail            |
|:------------:|:---------:|:--------------------------:|
| SpeckledBand |  stories  |            ...             |
|     ...      |    ...    |            ...             |
|    \<bos>    |  \<bos>   |           \<bos>           |
|  \<unknown>  | predicate |            kill            |
|  \<unknown>  |   whom    |           Julia            |
|  \<unknown>  |  subject  | \<mask(Answer is Roylott)> |
|  \<unknown>  |    why    |          \<mask>           |
|  \<unknown>  |   what    |          \<mask>           |
|  \<unknown>  |   when    |          \<mask>           |

In [17]:
def do_SpeckledBand_pred():
    title = 'SpeckledBand'
    victim_name = 'Julia'
    killer_name = 'Roylott'
    last_index = 401
    story_len = 80

    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention
do_SpeckledBand_pred()
pass

2023-02-03 04:59:28 - INFO - 2806554648.py - 12 - The pred ranking about SpeckledBand:Roylott is 0


predicate                           whom  \
0      word.predicate:hear           SpeckledBand:Roylott   
1        word.predicate:go             SpeckledBand:Helen   
2       word.predicate:see             SpeckledBand:snake   
3     word.predicate:think                AllTitle:Watson   
4       word.predicate:say    SilverBlaze:Fitzroy_Simpson   
5      word.predicate:find  AbbeyGrange:Lady_Brackenstall   
6     word.predicate:exist                AllTitle:Holmes   
7   word.predicate:receive            AbbeyGrange:Theresa   
8      word.predicate:meet             CrookedMan:Barclay   
9     word.predicate:leave              DevilsFoot:Brenda   
10         AllTitle:Holmes   DateTime:1883-04-01T14:00:00   
11     word.predicate:have        SilverBlaze:Silas_Brown   
12  word.predicate:examine     ResidentPatient:Helper_boy   
13   word.predicate:return  AbbeyGrange:Thought_of_Holmes   
14    word.predicate:enter   DateTime:1883-04-01T15:00:00   
15     word.predicate:open        word.predicate:notExist   
16     word.predicate:send            DevilsFoot:Roundhay   
17       DevilsFoot:Brenda            DevilsFoot:Mortimer   
18      word.predicate:put   SpeckledBand:VentilationHole   
19     word.predicate:call   SpeckledBand:Helen_s_bedroom   

                          subject                                   why  \
0            SpeckledBand:Roylott                     SpeckledBand:safe   
1     SilverBlaze:Fitzroy_Simpson        SpeckledBand:Roylott_s_bedroom   
2              SpeckledBand:snake          SpeckledBand:VentilationHole   
3                 AllTitle:Holmes            ResidentPatient:Helper_boy   
4              SpeckledBand:Helen                    SpeckledBand:Helen   
5                 AllTitle:Watson          DateTime:1883-04-01T17:00:00   
6   AbbeyGrange:Lady_Brackenstall         AbbeyGrange:Lady_Brackenstall   
7            DevilsFoot:Sterndale           AbbeyGrange:Stanley_Hopkins   
8    DateTime:1883-04-01T14:00:00                      AbbeyGrange:1895   
9             AbbeyGrange:Theresa            SpeckledBand:1883-04-01T17   
10                DevilsFoot:Owen                       AllTitle:Watson   
11              DevilsFoot:Brenda               SpeckledBand:1873-04-01   
12               DancingMen:Elsie                      SpeckledBand:bed   
13        SilverBlaze:Silas_Brown                  AbbeyGrange:Sydenham   
14        word.predicate:notExist                     AbbeyGrange:truth   
15            DevilsFoot:Mortimer  AbbeyGrange:Sir_Eustace_Brackenstall   
16        AbbeyGrange:Jack_Croker         AbbeyGrange:Thought_of_Watson   
17           SpeckledBand:coroner              SpeckledBand:round_table   
18     ResidentPatient:Helper_boy            SpeckledBand:1883-04-01T13   
19   SpeckledBand:Helen_s_bedroom               AbbeyGrange:dining_room   

                                    what                                 where  
0                     SpeckledBand:snake          SpeckledBand:Julia_s_bedroom  
1                     SpeckledBand:Helen        SpeckledBand:Roylott_s_bedroom  
2                     SpeckledBand:Julia       SpeckledBand:mansion_of_Roylott  
3                       SpeckledBand:bed                      CrookedMan:Nancy  
4                   SpeckledBand:handgun  AbbeyGrange:Sir_Eustace_Brackenstall  
5           SpeckledBand:VentilationHole                       AllTitle:Watson  
6                  SpeckledBand:dog_whip                      SpeckledBand:bed  
7         SpeckledBand:Roylott_s_bedroom         AbbeyGrange:Lady_Brackenstall  
8               DancingMen:Dancing_dolls               AbbeyGrange:dining_room  
9   AbbeyGrange:Sir_Eustace_Brackenstall                               <bos_e>  
10          DateTime:1883-04-01T15:00:00                  word.predicate:think  
11                       AllTitle:Watson                       AllTitle:Holmes  
12                   AbbeyGrange:Theresa                    SpeckledBand:Julia  
13                  Speck

index=452, triple=['SpeckledBand:401', 'kgc:subject', 'SpeckledBand:Roma'], attention list


head          relation  \
444  SpeckledBand:399          kgc:time   
429  SpeckledBand:397       kgc:subject   
401  SpeckledBand:391          kgc:time   
452  SpeckledBand:401       kgc:subject   
328  SpeckledBand:377       kgc:subject   
299  SpeckledBand:372          kgc:when   
321  SpeckledBand:376       kgc:subject   
293  SpeckledBand:371          kgc:when   
427  SpeckledBand:396          kgc:time   
450  SpeckledBand:400          kgc:time   
288  SpeckledBand:370          kgc:time   
369  SpeckledBand:385       kgc:subject   
304  SpeckledBand:373          kgc:when   
446  SpeckledBand:400       kgc:subject   
337  SpeckledBand:378          kgc:when   
120  SpeckledBand:341          kgc:time   
365  SpeckledBand:384       kgc:subject   
294  SpeckledBand:371          kgc:time   
421  SpeckledBand:395          kgc:time   
332  SpeckledBand:377          kgc:when   
310  SpeckledBand:374          kgc:when   
300  SpeckledBand:372          kgc:time   
396  SpeckledBand:391       kgc:subject   
335  SpeckledBand:378       kgc:subject   
343  SpeckledBand:379          kgc:when   
438  SpeckledBand:398          kgc:time   
313  SpeckledBand:375       kgc:subject   
252  SpeckledBand:365       kgc:subject   
296  SpeckledBand:372       kgc:subject   
325  SpeckledBand:376          kgc:when   
455          <mask_e>    kgc:infoSource   
239  SpeckledBand:363       kgc:subject   
390  SpeckledBand:390       kgc:subject   
434  SpeckledBand:398       kgc:subject   
403  SpeckledBand:392       kgc:subject   
268  SpeckledBand:367          kgc:time   
457          <mask_e>          kgc:whom   
186  SpeckledBand:354       kgc:subject   
432  SpeckledBand:397          kgc:time   
382  SpeckledBand:388       kgc:subject   
307  SpeckledBand:374       kgc:subject   
362  SpeckledBand:383          kgc:when   
363  SpeckledBand:383          kgc:time   
412  SpeckledBand:394       kgc:subject   
127  SpeckledBand:343          kgc:time   
380  SpeckledBand:387          kgc:whom   
270  SpeckledBand:368       kgc:subject   
311  SpeckledBand:374          kgc:time   
440  SpeckledBand:399       kgc:subject   
133  SpeckledBand:344          kgc:time   
420  SpeckledBand:395          kgc:when   
22   SpeckledBand:325    kgc:infoSource   
333  SpeckledBand:377          kgc:time   
318  SpeckledBand:375          kgc:when   
373  SpeckledBand:386       kgc:subject   
227  SpeckledBand:361       kgc:subject   
245  SpeckledBand:364       kgc:subject   
290  SpeckledBand:371       kgc:subject   
305  SpeckledBand:373          kgc:time   
213  SpeckledBand:358          kgc:time   
458          <mask_e>       kgc:subject   
426  SpeckledBand:396          kgc:when   
262  SpeckledBand:366          kgc:time   
377  SpeckledBand:387       kgc:subject   
415  SpeckledBand:394          kgc:when   
171  SpeckledBand:351          kgc:time   
209  SpeckledBand:358       kgc:subject   
250  SpeckledBand:364          kgc:time   
157  SpeckledBand:349       kgc:subject   
302  SpeckledBand:373       kgc:subject   
241  SpeckledBand:363    kgc:infoSource   
225  SpeckledBand:360          kgc:time   
282  SpeckledBand:370       kgc:subject   
247  SpeckledBand:364          kgc:whom   
338  SpeckledBand:378          kgc:time   
37   SpeckledBand:327          kgc:time   
449  SpeckledBand:400          kgc:when   
219  SpeckledBand:359          kgc:time   
274  SpeckledBand:368          kgc:time   
90   SpeckledBand:336          kgc:time   
425  SpeckledBand:396          kgc:what   
138  SpeckledBand:345          kgc:time   
276  SpeckledBand:369       kgc:subject   
423  SpeckledBand:396       kgc:subject   
356  SpeckledBand:383       kgc:subject   
107  SpeckledBand:339          kgc:time   
386  SpeckledBand:389       kgc:subject   
391  SpeckledBand:390       kgc:subject   
443  SpeckledBand:399          kgc:when   
113  SpeckledBand:340          kgc:time   
24   SpeckledBand:325          kgc:time   
190  SpeckledBand:354          kgc:time   
160  SpeckledBand:

index=453, triple=['SpeckledBand:401', 'kgc:hasProperty', 'word.predicate:band'], attention list


...

head          relation  \
390  SpeckledBand:390       kgc:subject   
391  SpeckledBand:390       kgc:subject   
299  SpeckledBand:372          kgc:when   
296  SpeckledBand:372       kgc:subject   
346  SpeckledBand:380       kgc:subject   
126  SpeckledBand:343          kgc:when   
165  SpeckledBand:350          kgc:when   
457          <mask_e>          kgc:whom   
392  SpeckledBand:390       kgc:subject   
300  SpeckledBand:372          kgc:time   
168  SpeckledBand:351       kgc:subject   
122  SpeckledBand:343       kgc:subject   
458          <mask_e>       kgc:subject   
459          <mask_e>           kgc:why   
302  SpeckledBand:373       kgc:subject   
294  SpeckledBand:371          kgc:time   
268  SpeckledBand:367          kgc:time   
343  SpeckledBand:379          kgc:when   
127  SpeckledBand:343          kgc:time   
440  SpeckledBand:399       kgc:subject   
427  SpeckledBand:396          kgc:time   
304  SpeckledBand:373          kgc:when   
438  SpeckledBand:398          kgc:time   
137  SpeckledBand:345          kgc:when   
307  SpeckledBand:374       kgc:subject   
120  SpeckledBand:341          kgc:time   
288  SpeckledBand:370          kgc:time   
293  SpeckledBand:371          kgc:when   
166  SpeckledBand:350          kgc:time   
162  SpeckledBand:350       kgc:subject   
106  SpeckledBand:339          kgc:when   
432  SpeckledBand:397          kgc:time   
384  SpeckledBand:388            kgc:on   
386  SpeckledBand:389       kgc:subject   
437  SpeckledBand:398          kgc:when   
396  SpeckledBand:391       kgc:subject   
112  SpeckledBand:340          kgc:when   
410  SpeckledBand:393          kgc:when   
274  SpeckledBand:368          kgc:time   
204  SpeckledBand:357       kgc:subject   
335  SpeckledBand:378       kgc:subject   
452  SpeckledBand:401       kgc:subject   
401  SpeckledBand:391          kgc:time   
206  SpeckledBand:357          kgc:when   
394  SpeckledBand:390         kgc:where   
132  SpeckledBand:344          kgc:when   
434  SpeckledBand:398       kgc:subject   
311  SpeckledBand:374          kgc:time   
184  SpeckledBand:353          kgc:time   
273  SpeckledBand:368          kgc:when   
104  SpeckledBand:339   kgc:hasProperty   
250  SpeckledBand:364          kgc:time   
170  SpeckledBand:351          kgc:when   
207  SpeckledBand:357          kgc:time   
124  SpeckledBand:343         kgc:where   
444  SpeckledBand:399          kgc:time   
443  SpeckledBand:399          kgc:when   
460          <mask_e>          kgc:what   
337  SpeckledBand:378          kgc:when   
305  SpeckledBand:373          kgc:time   
369  SpeckledBand:385       kgc:subject   
313  SpeckledBand:375       kgc:subject   
344  SpeckledBand:379          kgc:time   
270  SpeckledBand:368       kgc:subject   
409  SpeckledBand:393          kgc:what   
421  SpeckledBand:395          kgc:time   
133  SpeckledBand:344          kgc:time   
262  SpeckledBand:366          kgc:time   
107  SpeckledBand:339          kgc:time   
245  SpeckledBand:364       kgc:subject   
349  SpeckledBand:381       kgc:subject   
202  SpeckledBand:356          kgc:time   
179  SpeckledBand:352          kgc:time   
119  SpeckledBand:341          kgc:when   
340  SpeckledBand:379       kgc:subject   
113  SpeckledBand:340          kgc:time   
287  SpeckledBand:370          kgc:when   
310  SpeckledBand:374          kgc:when   
303  SpeckledBand:373   kgc:hasProperty   
455          <mask_e>    kgc:infoSource   
138  SpeckledBand:345          kgc:time   
407  SpeckledBand:393       kgc:subject   
181  SpeckledBand:353       kgc:subject   
209  SpeckledBand:358       kgc:subject   
171  SpeckledBand:351          kgc:time   
183  SpeckledBand:353          kgc:when   
111  SpeckledBand:340          kgc:what   
338  SpeckledBand:378          kgc:time   
125  SpeckledBand:343            kgc:on   
186  SpeckledBand:354       kgc:subject   
169  SpeckledBand:351   kgc:hasProperty   
160  SpeckledBand:349          kgc:time   
405  SpeckledBand:

index=460, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
120  SpeckledBand:341          kgc:time   
127  SpeckledBand:343          kgc:time   
294  SpeckledBand:371          kgc:time   
390  SpeckledBand:390       kgc:subject   
133  SpeckledBand:344          kgc:time   
382  SpeckledBand:388       kgc:subject   
300  SpeckledBand:372          kgc:time   
457          <mask_e>          kgc:whom   
299  SpeckledBand:372          kgc:when   
444  SpeckledBand:399          kgc:time   
262  SpeckledBand:366          kgc:time   
458          <mask_e>       kgc:subject   
288  SpeckledBand:370          kgc:time   
268  SpeckledBand:367          kgc:time   
296  SpeckledBand:372       kgc:subject   
113  SpeckledBand:340          kgc:time   
335  SpeckledBand:378       kgc:subject   
438  SpeckledBand:398          kgc:time   
166  SpeckledBand:350          kgc:time   
391  SpeckledBand:390       kgc:subject   
171  SpeckledBand:351          kgc:time   
196  SpeckledBand:355          kgc:time   
427  SpeckledBand:396          kgc:time   
401  SpeckledBand:391          kgc:time   
138  SpeckledBand:345          kgc:time   
455          <mask_e>    kgc:infoSource   
237  SpeckledBand:362          kgc:time   
107  SpeckledBand:339          kgc:time   
450  SpeckledBand:400          kgc:time   
384  SpeckledBand:388            kgc:on   
392  SpeckledBand:390       kgc:subject   
160  SpeckledBand:349          kgc:time   
207  SpeckledBand:357          kgc:time   
311  SpeckledBand:374          kgc:time   
337  SpeckledBand:378          kgc:when   
333  SpeckledBand:377          kgc:time   
202  SpeckledBand:356          kgc:time   
380  SpeckledBand:387          kgc:whom   
250  SpeckledBand:364          kgc:time   
179  SpeckledBand:352          kgc:time   
184  SpeckledBand:353          kgc:time   
90   SpeckledBand:336          kgc:time   
421  SpeckledBand:395          kgc:time   
386  SpeckledBand:389       kgc:subject   
274  SpeckledBand:368          kgc:time   
338  SpeckledBand:378          kgc:time   
293  SpeckledBand:371          kgc:when   
373  SpeckledBand:386       kgc:subject   
452  SpeckledBand:401       kgc:subject   
304  SpeckledBand:373          kgc:when   
219  SpeckledBand:359          kgc:time   
168  SpeckledBand:351       kgc:subject   
305  SpeckledBand:373          kgc:time   
432  SpeckledBand:397          kgc:time   
346  SpeckledBand:380       kgc:subject   
344  SpeckledBand:379          kgc:time   
225  SpeckledBand:360          kgc:time   
343  SpeckledBand:379          kgc:when   
290  SpeckledBand:371       kgc:subject   
369  SpeckledBand:385       kgc:subject   
245  SpeckledBand:364       kgc:subject   
377  SpeckledBand:387       kgc:subject   
440  SpeckledBand:399       kgc:subject   
243  SpeckledBand:363          kgc:time   
200  SpeckledBand:356          kgc:what   
231  SpeckledBand:361          kgc:time   
396  SpeckledBand:391       kgc:subject   
403  SpeckledBand:392       kgc:subject   
313  SpeckledBand:375       kgc:subject   
256  SpeckledBand:365          kgc:time   
446  SpeckledBand:400       kgc:subject   
321  SpeckledBand:376       kgc:subject   
213  SpeckledBand:358          kgc:time   
190  SpeckledBand:354          kgc:time   
319  SpeckledBand:375          kgc:time   
101  SpeckledBand:338          kgc:time   
459          <mask_e>           kgc:why   
302  SpeckledBand:373       kgc:subject   
247  SpeckledBand:364          kgc:whom   
347  SpeckledBand:380   kgc:hasProperty   
303  SpeckledBand:373   kgc:hasProperty   
209  SpeckledBand:358       kgc:subject   
328  SpeckledBand:377       kgc:subject   
95   SpeckledBand:337          kgc:time   
206  SpeckledBand:357          kgc:when   
149  SpeckledBand:347          kgc:time   
340  SpeckledBand:379       kgc:subject   
434  SpeckledBand:398       kgc:subject   
157  SpeckledBand:349       kgc:subject   
143  SpeckledBand:346          kgc:time   
186  SpeckledBand:354       kgc:subject   
363  SpeckledBand:383          kgc:time   
22   SpeckledBand:

index=461, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
296  SpeckledBand:372       kgc:subject   
299  SpeckledBand:372          kgc:when   
300  SpeckledBand:372          kgc:time   
390  SpeckledBand:390       kgc:subject   
104  SpeckledBand:339   kgc:hasProperty   
391  SpeckledBand:390       kgc:subject   
401  SpeckledBand:391          kgc:time   
304  SpeckledBand:373          kgc:when   
302  SpeckledBand:373       kgc:subject   
127  SpeckledBand:343          kgc:time   
294  SpeckledBand:371          kgc:time   
410  SpeckledBand:393          kgc:when   
457          <mask_e>          kgc:whom   
343  SpeckledBand:379          kgc:when   
120  SpeckledBand:341          kgc:time   
444  SpeckledBand:399          kgc:time   
165  SpeckledBand:350          kgc:when   
337  SpeckledBand:378          kgc:when   
335  SpeckledBand:378       kgc:subject   
455          <mask_e>    kgc:infoSource   
133  SpeckledBand:344          kgc:time   
307  SpeckledBand:374       kgc:subject   
107  SpeckledBand:339          kgc:time   
126  SpeckledBand:343          kgc:when   
458          <mask_e>       kgc:subject   
268  SpeckledBand:367          kgc:time   
305  SpeckledBand:373          kgc:time   
138  SpeckledBand:345          kgc:time   
245  SpeckledBand:364       kgc:subject   
438  SpeckledBand:398          kgc:time   
166  SpeckledBand:350          kgc:time   
262  SpeckledBand:366          kgc:time   
168  SpeckledBand:351       kgc:subject   
392  SpeckledBand:390       kgc:subject   
293  SpeckledBand:371          kgc:when   
427  SpeckledBand:396          kgc:time   
450  SpeckledBand:400          kgc:time   
432  SpeckledBand:397          kgc:time   
440  SpeckledBand:399       kgc:subject   
340  SpeckledBand:379       kgc:subject   
101  SpeckledBand:338          kgc:time   
196  SpeckledBand:355          kgc:time   
274  SpeckledBand:368          kgc:time   
396  SpeckledBand:391       kgc:subject   
421  SpeckledBand:395          kgc:time   
313  SpeckledBand:375       kgc:subject   
346  SpeckledBand:380       kgc:subject   
311  SpeckledBand:374          kgc:time   
250  SpeckledBand:364          kgc:time   
202  SpeckledBand:356          kgc:time   
207  SpeckledBand:357          kgc:time   
122  SpeckledBand:343       kgc:subject   
184  SpeckledBand:353          kgc:time   
160  SpeckledBand:349          kgc:time   
443  SpeckledBand:399          kgc:when   
288  SpeckledBand:370          kgc:time   
344  SpeckledBand:379          kgc:time   
333  SpeckledBand:377          kgc:time   
169  SpeckledBand:351   kgc:hasProperty   
237  SpeckledBand:362          kgc:time   
452  SpeckledBand:401       kgc:subject   
113  SpeckledBand:340          kgc:time   
434  SpeckledBand:398       kgc:subject   
338  SpeckledBand:378          kgc:time   
225  SpeckledBand:360          kgc:time   
171  SpeckledBand:351          kgc:time   
206  SpeckledBand:357          kgc:when   
394  SpeckledBand:390         kgc:where   
243  SpeckledBand:363          kgc:time   
186  SpeckledBand:354       kgc:subject   
437  SpeckledBand:398          kgc:when   
321  SpeckledBand:376       kgc:subject   
407  SpeckledBand:393       kgc:subject   
303  SpeckledBand:373   kgc:hasProperty   
273  SpeckledBand:368          kgc:when   
90   SpeckledBand:336          kgc:time   
106  SpeckledBand:339          kgc:when   
190  SpeckledBand:354          kgc:time   
162  SpeckledBand:350       kgc:subject   
400  SpeckledBand:391          kgc:when   
205  SpeckledBand:357   kgc:hasProperty   
37   SpeckledBand:327          kgc:time   
310  SpeckledBand:374          kgc:when   
382  SpeckledBand:388       kgc:subject   
256  SpeckledBand:365          kgc:time   
318  SpeckledBand:375          kgc:when   
137  SpeckledBand:345          kgc:when   
247  SpeckledBand:364          kgc:whom   
290  SpeckledBand:371       kgc:subject   
95   SpeckledBand:337          kgc:time   
446  SpeckledBand:400       kgc:subject   
17   SpeckledBand:324          kgc:time   
270  SpeckledBand:

### DevilsFoot(悪魔の足跡１)
Who killed the victims? (criminal & explanation)
被害者: Brenda
犯人: Mortimer
犯行動機: 財産

In [18]:
def do_devil1_pred():
    title = 'DevilsFoot'
    victim_name = 'Brenda'
    killer_name = 'Mortimer'
    last_index = 489
    story_len = 80
    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_devil1_pred()
pass

2023-02-03 04:59:29 - INFO - 2806554648.py - 12 - The pred ranking about DevilsFoot:Mortimer is 1


predicate                             whom  \
0     DevilsFoot:Sterndale             DevilsFoot:Sterndale   
1        word.predicate:go              DevilsFoot:Mortimer   
2       word.predicate:say                  AllTitle:Holmes   
3      word.predicate:kill                  AllTitle:Watson   
4      word.predicate:have                  DevilsFoot:Owen   
5   word.predicate:notHave                DevilsFoot:Brenda   
6     word.predicate:exist                 CrookedMan:Nancy   
7      word.predicate:find  ResidentPatient:Percy_Trevelyan   
8    word.predicate:return       ResidentPatient:Helper_boy   
9        DevilsFoot:George          AbbeyGrange:Jack_Croker   
10         AllTitle:Holmes                DevilsFoot:George   
11     word.predicate:live                  DevilsFoot:lamp   
12   word.predicate:become               CrookedMan:Barclay   
13     word.predicate:hear                  CrookedMan:Jane   
14    word.predicate:think                  DevilsFoot:room   
15      word.predicate:die          word.predicate:notExist   
16     word.predicate:meet              CrookedMan:coachman   
17    word.predicate:shoot         SilverBlaze:Silver_Blaze   
18     DevilsFoot:Mortimer               SpeckledBand:Helen   
19     word.predicate:open          SilverBlaze:Silas_Brown   

                            subject                                   why  \
0              DevilsFoot:Sterndale                  DevilsFoot:Sterndale   
1               DevilsFoot:Mortimer                       CrookedMan:Jane   
2                   AllTitle:Watson                   DevilsFoot:Cornwall   
3                 DevilsFoot:George            ResidentPatient:Helper_boy   
4                   DevilsFoot:Owen               AbbeyGrange:Jack_Croker   
5                 SilverBlaze:Gypsy                ACaseOfIdentity:letter   
6           AbbeyGrange:Jack_Croker              SilverBlaze:Silver_Blaze   
7                   AllTitle:Holmes                    SpeckledBand:Helen   
8                   DevilsFoot:room            word.predicate:unconscious   
9     SilverBlaze:Gregory_Inspector                CrookedMan:living_room   
10       ResidentPatient:Helper_boy                      DevilsFoot:table   
11  ResidentPatient:Percy_Trevelyan                       DevilsFoot:lamp   
12                DevilsFoot:Brenda  ResidentPatient:East_Indies_colonial   
13          SilverBlaze:Silas_Brown                   DevilsFoot:Criminal   
14               SpeckledBand:Helen                    SilverBlaze:police   
15            DancingMen:Abe_Slaney   ACaseOfIdentity:money_of_Sutherland   
16                word.predicate:go                      DancingMen:Elsie   
17              CrookedMan:coachman                 ResidentPatient:Youth   
18         SilverBlaze:Silver_Blaze                       AllTitle:Watson   
19                  CrookedMan:Jane          DateTime:1887-07-06T21:15:00   

                                  what                                 where  
0                 DevilsFoot:Sterndale                   DevilsFoot:Cornwall  
1           ResidentPatient:Helper_boy                       AllTitle:Holmes  
2             SilverBlaze:Silver_Blaze                  DevilsFoot:Sterndale  
3               CrookedMan:living_room                CrookedMan:living_room  
4                    SilverBlaze:Gypsy     DevilsFoot:cottage_of_Pordeux_Bay  
5          ResidentPatient:Elderly_man           ResidentPatient:Elderly_man  
6               ACaseOfIdentity:letter                DevilsFoot:living_room  
7              AbbeyGrange:Jack_Croker                     SilverBlaze:Gypsy  
8                       DevilsFoot:459              SilverBlaze:Silver_Blaze  
9               DevilsFoot:living_room                    CrookedMan:Barclay  
10                 DevilsFoot:Cornwall            ResidentPatient:Helper_boy  
11                     DevilsFoot:lamp                       AllTitle:Watson  
12         ACaseOfIdentity:Plush_weave          

index=444, triple=['DevilsFoot:489', 'kgc:what', 'DevilsFoot:gravel'], attention list


head          relation  \
421  DevilsFoot:484         kgc:where   
424  DevilsFoot:485       kgc:subject   
252  DevilsFoot:453       kgc:subject   
445  DevilsFoot:489         kgc:where   
174  DevilsFoot:439            kgc:to   
419  DevilsFoot:484       kgc:subject   
256  DevilsFoot:454       kgc:subject   
258  DevilsFoot:454            kgc:to   
408  DevilsFoot:482       kgc:subject   
411  DevilsFoot:482            kgc:to   
429  DevilsFoot:486       kgc:subject   
149  DevilsFoot:435       kgc:subject   
440  DevilsFoot:488         kgc:where   
410  DevilsFoot:482          kgc:what   
452        <mask_e>          kgc:what   
451        <mask_e>           kgc:why   
55   DevilsFoot:418       kgc:subject   
242  DevilsFoot:451       kgc:subject   
414  DevilsFoot:483       kgc:subject   
403  DevilsFoot:481       kgc:subject   
261  DevilsFoot:455       kgc:subject   
394  DevilsFoot:479       kgc:subject   
254  DevilsFoot:453    kgc:infoSource   
405  DevilsFoot:481    kgc:infoSource   
392  DevilsFoot:478            kgc:on   
427  DevilsFoot:485    kgc:infoSource   
284  DevilsFoot:459           kgc:why   
422  DevilsFoot:484    kgc:infoSource   
453        <mask_e>         kgc:where   
165  DevilsFoot:438       kgc:subject   
248  DevilsFoot:452       kgc:subject   
143  DevilsFoot:434       kgc:subject   
266  DevilsFoot:456       kgc:subject   
244  DevilsFoot:451         kgc:where   
275  DevilsFoot:458       kgc:subject   
172  DevilsFoot:439       kgc:subject   
52   DevilsFoot:417          kgc:what   
376  DevilsFoot:475       kgc:subject   
175  DevilsFoot:439    kgc:infoSource   
333  DevilsFoot:469       kgc:subject   
438  DevilsFoot:488       kgc:subject   
117  DevilsFoot:428       kgc:subject   
42   DevilsFoot:415         kgc:where   
313  DevilsFoot:465       kgc:subject   
426  DevilsFoot:485          kgc:what   
412  DevilsFoot:482    kgc:infoSource   
202  DevilsFoot:444          kgc:what   
318  DevilsFoot:466       kgc:subject   
434  DevilsFoot:487       kgc:subject   
153  DevilsFoot:436       kgc:subject   
62   DevilsFoot:419       kgc:subject   
444  DevilsFoot:489          kgc:what   
450        <mask_e>       kgc:subject   
200  DevilsFoot:444       kgc:subject   
245  DevilsFoot:451    kgc:infoSource   
417  DevilsFoot:483    kgc:infoSource   
383  DevilsFoot:476    kgc:infoSource   
40   DevilsFoot:415       kgc:subject   
192  DevilsFoot:442          kgc:whom   
310  DevilsFoot:464          kgc:what   
138  DevilsFoot:433       kgc:subject   
169  DevilsFoot:438          kgc:whom   
308  DevilsFoot:464       kgc:subject   
126  DevilsFoot:430       kgc:subject   
268  DevilsFoot:456          kgc:what   
431  DevilsFoot:486    kgc:infoSource   
350  DevilsFoot:472       kgc:subject   
271  DevilsFoot:457       kgc:subject   
436  DevilsFoot:487            kgc:on   
167  DevilsFoot:438          kgc:whom   
382  DevilsFoot:476          kgc:what   
398  DevilsFoot:480       kgc:subject   
314  DevilsFoot:465       kgc:subject   
396  DevilsFoot:479    kgc:infoSource   
406  DevilsFoot:481          kgc:from   
442  DevilsFoot:489       kgc:subject   
121  DevilsFoot:429       kgc:subject   
321  DevilsFoot:466    kgc:infoSource   
154  DevilsFoot:436       kgc:subject   
45   DevilsFoot:416       kgc:subject   
43   DevilsFoot:415    kgc:infoSource   
385  DevilsFoot:477       kgc:subject   
269  DevilsFoot:456    kgc:infoSource   
297  DevilsFoot:462       kgc:subject   
380  DevilsFoot:476       kgc:subject   
250  DevilsFoot:452          kgc:what   
328  DevilsFoot:468       kgc:subject   
132  DevilsFoot:431          kgc:what   
294  DevilsFoot:461          kgc:whom   
59   DevilsFoot:418          kgc:when   
416  DevilsFoot:483          kgc:what   
140  DevilsFoot:433         kgc:where   
146  DevilsFoot:434          kgc:what   
180  DevilsFoot:440       kgc:subject   
151  DevilsFoot:435         kgc:where   
155  DevilsFoot:436       kgc:subject   
447        <mask_e>    kgc:infoSource 

index=445, triple=['DevilsFoot:489', 'kgc:where', 'DevilsFoot:garden_of_Cottage_of_Sterndale'], attention list


...

head          relation  \
408  DevilsFoot:482       kgc:subject   
55   DevilsFoot:418       kgc:subject   
271  DevilsFoot:457       kgc:subject   
42   DevilsFoot:415         kgc:where   
403  DevilsFoot:481       kgc:subject   
429  DevilsFoot:486       kgc:subject   
438  DevilsFoot:488       kgc:subject   
275  DevilsFoot:458       kgc:subject   
434  DevilsFoot:487       kgc:subject   
411  DevilsFoot:482            kgc:to   
256  DevilsFoot:454       kgc:subject   
138  DevilsFoot:433       kgc:subject   
149  DevilsFoot:435       kgc:subject   
143  DevilsFoot:434       kgc:subject   
436  DevilsFoot:487            kgc:on   
252  DevilsFoot:453       kgc:subject   
67   DevilsFoot:420       kgc:subject   
453        <mask_e>         kgc:where   
141  DevilsFoot:433    kgc:infoSource   
273  DevilsFoot:457    kgc:infoSource   
414  DevilsFoot:483       kgc:subject   
34   DevilsFoot:414       kgc:subject   
419  DevilsFoot:484       kgc:subject   
313  DevilsFoot:465       kgc:subject   
172  DevilsFoot:439       kgc:subject   
62   DevilsFoot:419       kgc:subject   
134  DevilsFoot:432       kgc:subject   
333  DevilsFoot:469       kgc:subject   
376  DevilsFoot:475       kgc:subject   
140  DevilsFoot:433         kgc:where   
380  DevilsFoot:476       kgc:subject   
424  DevilsFoot:485       kgc:subject   
40   DevilsFoot:415       kgc:subject   
58   DevilsFoot:418          kgc:when   
60   DevilsFoot:418          kgc:time   
59   DevilsFoot:418          kgc:when   
147  DevilsFoot:434    kgc:infoSource   
126  DevilsFoot:430       kgc:subject   
412  DevilsFoot:482    kgc:infoSource   
136  DevilsFoot:432    kgc:infoSource   
117  DevilsFoot:428       kgc:subject   
440  DevilsFoot:488         kgc:where   
405  DevilsFoot:481    kgc:infoSource   
244  DevilsFoot:451         kgc:where   
242  DevilsFoot:451       kgc:subject   
308  DevilsFoot:464       kgc:subject   
394  DevilsFoot:479       kgc:subject   
410  DevilsFoot:482          kgc:what   
269  DevilsFoot:456    kgc:infoSource   
314  DevilsFoot:465       kgc:subject   
103  DevilsFoot:425       kgc:subject   
254  DevilsFoot:453    kgc:infoSource   
421  DevilsFoot:484         kgc:where   
153  DevilsFoot:436       kgc:subject   
318  DevilsFoot:466       kgc:subject   
266  DevilsFoot:456       kgc:subject   
174  DevilsFoot:439            kgc:to   
121  DevilsFoot:429       kgc:subject   
258  DevilsFoot:454            kgc:to   
151  DevilsFoot:435         kgc:where   
45   DevilsFoot:416       kgc:subject   
270         <bos_e>           <bos_r>   
43   DevilsFoot:415    kgc:infoSource   
450        <mask_e>       kgc:subject   
311  DevilsFoot:464    kgc:infoSource   
306  DevilsFoot:463    kgc:infoSource   
431  DevilsFoot:486    kgc:infoSource   
255         <bos_e>           <bos_r>   
260         <bos_e>           <bos_r>   
53   DevilsFoot:417    kgc:infoSource   
312         <bos_e>           <bos_r>   
261  DevilsFoot:455       kgc:subject   
137         <bos_e>           <bos_r>   
274         <bos_e>           <bos_r>   
301         <bos_e>           <bos_r>   
307         <bos_e>           <bos_r>   
422  DevilsFoot:484    kgc:infoSource   
165  DevilsFoot:438       kgc:subject   
296         <bos_e>           <bos_r>   
328  DevilsFoot:468       kgc:subject   
279  DevilsFoot:458    kgc:infoSource   
398  DevilsFoot:480       kgc:subject   
130  DevilsFoot:431       kgc:subject   
407         <bos_e>           <bos_r>   
52   DevilsFoot:417          kgc:what   
265         <bos_e>           <bos_r>   
317         <bos_e>           <bos_r>   
372  DevilsFoot:474       kgc:subject   
327         <bos_e>           <bos_r>   
248  DevilsFoot:452       kgc:subject   
451        <mask_e>           kgc:why   
437         <bos_e>           <bos_r>   
251         <bos_e>           <bos_r>   
241         <bos_e>           <bos_r>   
452        <mask_e>          kgc:what   
176  DevilsFoot:439          kgc:when   
142         <bos_e>           <bos_r> 

index=452, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
408  DevilsFoot:482       kgc:subject   
55   DevilsFoot:418       kgc:subject   
429  DevilsFoot:486       kgc:subject   
275  DevilsFoot:458       kgc:subject   
42   DevilsFoot:415         kgc:where   
403  DevilsFoot:481       kgc:subject   
434  DevilsFoot:487       kgc:subject   
424  DevilsFoot:485       kgc:subject   
438  DevilsFoot:488       kgc:subject   
410  DevilsFoot:482          kgc:what   
376  DevilsFoot:475       kgc:subject   
126  DevilsFoot:430       kgc:subject   
419  DevilsFoot:484       kgc:subject   
256  DevilsFoot:454       kgc:subject   
414  DevilsFoot:483       kgc:subject   
62   DevilsFoot:419       kgc:subject   
436  DevilsFoot:487            kgc:on   
333  DevilsFoot:469       kgc:subject   
149  DevilsFoot:435       kgc:subject   
411  DevilsFoot:482            kgc:to   
271  DevilsFoot:457       kgc:subject   
40   DevilsFoot:415       kgc:subject   
252  DevilsFoot:453       kgc:subject   
117  DevilsFoot:428       kgc:subject   
394  DevilsFoot:479       kgc:subject   
52   DevilsFoot:417          kgc:what   
67   DevilsFoot:420       kgc:subject   
121  DevilsFoot:429       kgc:subject   
254  DevilsFoot:453    kgc:infoSource   
141  DevilsFoot:433    kgc:infoSource   
34   DevilsFoot:414       kgc:subject   
380  DevilsFoot:476       kgc:subject   
412  DevilsFoot:482    kgc:infoSource   
431  DevilsFoot:486    kgc:infoSource   
453        <mask_e>         kgc:where   
405  DevilsFoot:481    kgc:infoSource   
242  DevilsFoot:451       kgc:subject   
143  DevilsFoot:434       kgc:subject   
421  DevilsFoot:484         kgc:where   
50   DevilsFoot:417       kgc:subject   
138  DevilsFoot:433       kgc:subject   
172  DevilsFoot:439       kgc:subject   
372  DevilsFoot:474       kgc:subject   
103  DevilsFoot:425       kgc:subject   
53   DevilsFoot:417    kgc:infoSource   
398  DevilsFoot:480       kgc:subject   
180  DevilsFoot:440       kgc:subject   
45   DevilsFoot:416       kgc:subject   
134  DevilsFoot:432       kgc:subject   
43   DevilsFoot:415    kgc:infoSource   
28   DevilsFoot:413       kgc:subject   
147  DevilsFoot:434    kgc:infoSource   
318  DevilsFoot:466       kgc:subject   
153  DevilsFoot:436       kgc:subject   
93   DevilsFoot:423       kgc:subject   
136  DevilsFoot:432    kgc:infoSource   
183  DevilsFoot:440    kgc:infoSource   
151  DevilsFoot:435         kgc:where   
273  DevilsFoot:457    kgc:infoSource   
422  DevilsFoot:484    kgc:infoSource   
427  DevilsFoot:485    kgc:infoSource   
60   DevilsFoot:418          kgc:time   
269  DevilsFoot:456    kgc:infoSource   
64   DevilsFoot:419    kgc:infoSource   
128  DevilsFoot:430          kgc:what   
450        <mask_e>       kgc:subject   
189  DevilsFoot:442       kgc:subject   
313  DevilsFoot:465       kgc:subject   
266  DevilsFoot:456       kgc:subject   
73   DevilsFoot:421       kgc:subject   
130  DevilsFoot:431       kgc:subject   
378  DevilsFoot:475    kgc:infoSource   
385  DevilsFoot:477       kgc:subject   
452        <mask_e>          kgc:what   
440  DevilsFoot:488         kgc:where   
435  DevilsFoot:487   kgc:hasProperty   
308  DevilsFoot:464       kgc:subject   
140  DevilsFoot:433         kgc:where   
328  DevilsFoot:468       kgc:subject   
336  DevilsFoot:469    kgc:infoSource   
175  DevilsFoot:439    kgc:infoSource   
451        <mask_e>           kgc:why   
382  DevilsFoot:476          kgc:what   
113  DevilsFoot:427       kgc:subject   
383  DevilsFoot:476    kgc:infoSource   
284  DevilsFoot:459           kgc:why   
187  DevilsFoot:441    kgc:infoSource   
167  DevilsFoot:438          kgc:whom   
279  DevilsFoot:458    kgc:infoSource   
132  DevilsFoot:431          kgc:what   
310  DevilsFoot:464          kgc:what   
174  DevilsFoot:439            kgc:to   
57   DevilsFoot:418    kgc:infoSource   
165  DevilsFoot:438       kgc:subject   
200  DevilsFoot:444       kgc:subject   
154  DevilsFoot:436       kgc:subject   
374  DevilsFoot:474    kgc:infoSource 

index=453, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
408  DevilsFoot:482       kgc:subject   
55   DevilsFoot:418       kgc:subject   
429  DevilsFoot:486       kgc:subject   
438  DevilsFoot:488       kgc:subject   
149  DevilsFoot:435       kgc:subject   
403  DevilsFoot:481       kgc:subject   
42   DevilsFoot:415         kgc:where   
434  DevilsFoot:487       kgc:subject   
256  DevilsFoot:454       kgc:subject   
252  DevilsFoot:453       kgc:subject   
333  DevilsFoot:469       kgc:subject   
271  DevilsFoot:457       kgc:subject   
453        <mask_e>         kgc:where   
275  DevilsFoot:458       kgc:subject   
242  DevilsFoot:451       kgc:subject   
308  DevilsFoot:464       kgc:subject   
126  DevilsFoot:430       kgc:subject   
380  DevilsFoot:476       kgc:subject   
172  DevilsFoot:439       kgc:subject   
424  DevilsFoot:485       kgc:subject   
411  DevilsFoot:482            kgc:to   
394  DevilsFoot:479       kgc:subject   
153  DevilsFoot:436       kgc:subject   
436  DevilsFoot:487            kgc:on   
117  DevilsFoot:428       kgc:subject   
141  DevilsFoot:433    kgc:infoSource   
60   DevilsFoot:418          kgc:time   
40   DevilsFoot:415       kgc:subject   
138  DevilsFoot:433       kgc:subject   
121  DevilsFoot:429       kgc:subject   
405  DevilsFoot:481    kgc:infoSource   
376  DevilsFoot:475       kgc:subject   
67   DevilsFoot:420       kgc:subject   
254  DevilsFoot:453    kgc:infoSource   
62   DevilsFoot:419       kgc:subject   
419  DevilsFoot:484       kgc:subject   
440  DevilsFoot:488         kgc:where   
328  DevilsFoot:468       kgc:subject   
58   DevilsFoot:418          kgc:when   
136  DevilsFoot:432    kgc:infoSource   
34   DevilsFoot:414       kgc:subject   
59   DevilsFoot:418          kgc:when   
431  DevilsFoot:486    kgc:infoSource   
134  DevilsFoot:432       kgc:subject   
414  DevilsFoot:483       kgc:subject   
143  DevilsFoot:434       kgc:subject   
140  DevilsFoot:433         kgc:where   
421  DevilsFoot:484         kgc:where   
273  DevilsFoot:457    kgc:infoSource   
57   DevilsFoot:418    kgc:infoSource   
53   DevilsFoot:417    kgc:infoSource   
302  DevilsFoot:463       kgc:subject   
103  DevilsFoot:425       kgc:subject   
151  DevilsFoot:435         kgc:where   
93   DevilsFoot:423       kgc:subject   
313  DevilsFoot:465       kgc:subject   
311  DevilsFoot:464    kgc:infoSource   
372  DevilsFoot:474       kgc:subject   
412  DevilsFoot:482    kgc:infoSource   
147  DevilsFoot:434    kgc:infoSource   
180  DevilsFoot:440       kgc:subject   
245  DevilsFoot:451    kgc:infoSource   
45   DevilsFoot:416       kgc:subject   
244  DevilsFoot:451         kgc:where   
43   DevilsFoot:415    kgc:infoSource   
410  DevilsFoot:482          kgc:what   
398  DevilsFoot:480       kgc:subject   
154  DevilsFoot:436       kgc:subject   
176  DevilsFoot:439          kgc:when   
28   DevilsFoot:413       kgc:subject   
175  DevilsFoot:439    kgc:infoSource   
432  DevilsFoot:486          kgc:when   
269  DevilsFoot:456    kgc:infoSource   
306  DevilsFoot:463    kgc:infoSource   
385  DevilsFoot:477       kgc:subject   
165  DevilsFoot:438       kgc:subject   
155  DevilsFoot:436       kgc:subject   
50   DevilsFoot:417       kgc:subject   
450        <mask_e>       kgc:subject   
200  DevilsFoot:444       kgc:subject   
183  DevilsFoot:440    kgc:infoSource   
383  DevilsFoot:476    kgc:infoSource   
248  DevilsFoot:452       kgc:subject   
266  DevilsFoot:456       kgc:subject   
130  DevilsFoot:431       kgc:subject   
258  DevilsFoot:454            kgc:to   
350  DevilsFoot:472       kgc:subject   
174  DevilsFoot:439            kgc:to   
427  DevilsFoot:485    kgc:infoSource   
318  DevilsFoot:466       kgc:subject   
422  DevilsFoot:484    kgc:infoSource   
237  DevilsFoot:450       kgc:subject   
261  DevilsFoot:455       kgc:subject   
168  DevilsFoot:438          kgc:whom   
343  DevilsFoot:471       kgc:subject   
221  DevilsFoot:447       kgc:subject   
64   DevilsFoot:419    kgc:infoSource 

### DevilsFoot(悪魔の足跡2)
Who killed the victims? (criminal & explanation)
被害者: Mortimer
犯人: 
犯行動機: 恋人の敵

In [19]:
def do_devil2_pred():
    title = 'DevilsFoot'
    victim_name = 'Mortimer'
    killer_name = 'Sterndale'
    last_index = 489
    story_len = 80
    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_devil2_pred()
pass

2023-02-03 04:59:30 - INFO - 2806554648.py - 12 - The pred ranking about DevilsFoot:Sterndale is 0


predicate                             whom  \
0           word.predicate:go                  AllTitle:Holmes   
1          word.predicate:say              DevilsFoot:Mortimer   
2        DevilsFoot:Sterndale                  AllTitle:Watson   
3         word.predicate:kill             DevilsFoot:Sterndale   
4       word.predicate:return  ResidentPatient:Percy_Trevelyan   
5             AllTitle:Holmes          SilverBlaze:Silas_Brown   
6         word.predicate:find                 CrookedMan:Nancy   
7        word.predicate:exist          word.predicate:notExist   
8         word.predicate:hear               CrookedMan:Barclay   
9         word.predicate:meet                  DevilsFoot:Owen   
10      word.predicate:become                  CrookedMan:Jane   
11       word.predicate:think              CrookedMan:coachman   
12          DevilsFoot:George                word.predicate:go   
13     word.predicate:notHave                DevilsFoot:window   
14        DevilsFoot:Mortimer                  DevilsFoot:lamp   
15       word.predicate:shoot                DevilsFoot:Brenda   
16  word.predicate:cannotFind         SilverBlaze:John_Straker   
17        word.predicate:have                  DevilsFoot:room   
18         word.predicate:die       ACaseOfIdentity:Sutherland   
19         word.predicate:ask              DevilsFoot:Roundhay   

                            subject                               why  \
0              DevilsFoot:Sterndale              DevilsFoot:Sterndale   
1               DevilsFoot:Mortimer                   CrookedMan:Jane   
2                   AllTitle:Watson               DevilsFoot:Cornwall   
3                   AllTitle:Holmes          SilverBlaze:Silver_Blaze   
4                   DevilsFoot:Owen                   DevilsFoot:lamp   
5                 DevilsFoot:George        ResidentPatient:Helper_boy   
6                 SilverBlaze:Gypsy                  DevilsFoot:table   
7   ResidentPatient:Percy_Trevelyan        word.predicate:unconscious   
8                   DevilsFoot:room            ACaseOfIdentity:letter   
9           AbbeyGrange:Jack_Croker           AbbeyGrange:Jack_Croker   
10       ResidentPatient:Helper_boy                SpeckledBand:Helen   
11    SilverBlaze:Gregory_Inspector            CrookedMan:living_room   
12          SilverBlaze:Silas_Brown                   AllTitle:Holmes   
13                DevilsFoot:Brenda                   DevilsFoot:room   
14              CrookedMan:coachman               DevilsFoot:Criminal   
15               SpeckledBand:Helen             ResidentPatient:Youth   
16            DancingMen:Abe_Slaney                 DevilsFoot:window   
17                word.predicate:go                SilverBlaze:police   
18                  CrookedMan:Jane  ResidentPatient:Examination_room   
19         SilverBlaze:Silver_Blaze               word.predicate:fire   

                                  what                              where  
0                 DevilsFoot:Sterndale                DevilsFoot:Cornwall  
1           ResidentPatient:Helper_boy                    AllTitle:Holmes  
2             SilverBlaze:Silver_Blaze               DevilsFoot:Sterndale  
3                    SilverBlaze:Gypsy  DevilsFoot:cottage_of_Pordeux_Bay  
4               CrookedMan:living_room             CrookedMan:living_room  
5                      DevilsFoot:lamp        ResidentPatient:Elderly_man  
6              AbbeyGrange:Jack_Croker                  SilverBlaze:Gypsy  
7               ACaseOfIdentity:letter             DevilsFoot:living_room  
8                       DevilsFoot:459           SilverBlaze:Silver_Blaze  
9          ResidentPatient:Elderly_man                 CrookedMan:Barclay  
10         ACaseOfIdentity:Plush_weave                  DevilsFoot:window  
11                     DevilsFoot:room                   DevilsFoot:table  
12                 DevilsFoot:Cornwall         ResidentPatient:Helper_boy  
13              DevilsFoot:living_r

index=444, triple=['DevilsFoot:489', 'kgc:what', 'DevilsFoot:gravel'], attention list


head          relation  \
421  DevilsFoot:484         kgc:where   
424  DevilsFoot:485       kgc:subject   
445  DevilsFoot:489         kgc:where   
252  DevilsFoot:453       kgc:subject   
174  DevilsFoot:439            kgc:to   
256  DevilsFoot:454       kgc:subject   
258  DevilsFoot:454            kgc:to   
419  DevilsFoot:484       kgc:subject   
408  DevilsFoot:482       kgc:subject   
429  DevilsFoot:486       kgc:subject   
411  DevilsFoot:482            kgc:to   
149  DevilsFoot:435       kgc:subject   
440  DevilsFoot:488         kgc:where   
410  DevilsFoot:482          kgc:what   
55   DevilsFoot:418       kgc:subject   
242  DevilsFoot:451       kgc:subject   
451        <mask_e>           kgc:why   
392  DevilsFoot:478            kgc:on   
403  DevilsFoot:481       kgc:subject   
394  DevilsFoot:479       kgc:subject   
453        <mask_e>         kgc:where   
414  DevilsFoot:483       kgc:subject   
261  DevilsFoot:455       kgc:subject   
254  DevilsFoot:453    kgc:infoSource   
452        <mask_e>          kgc:what   
427  DevilsFoot:485    kgc:infoSource   
405  DevilsFoot:481    kgc:infoSource   
284  DevilsFoot:459           kgc:why   
422  DevilsFoot:484    kgc:infoSource   
52   DevilsFoot:417          kgc:what   
244  DevilsFoot:451         kgc:where   
248  DevilsFoot:452       kgc:subject   
143  DevilsFoot:434       kgc:subject   
165  DevilsFoot:438       kgc:subject   
426  DevilsFoot:485          kgc:what   
175  DevilsFoot:439    kgc:infoSource   
172  DevilsFoot:439       kgc:subject   
266  DevilsFoot:456       kgc:subject   
376  DevilsFoot:475       kgc:subject   
275  DevilsFoot:458       kgc:subject   
202  DevilsFoot:444          kgc:what   
333  DevilsFoot:469       kgc:subject   
117  DevilsFoot:428       kgc:subject   
444  DevilsFoot:489          kgc:what   
313  DevilsFoot:465       kgc:subject   
438  DevilsFoot:488       kgc:subject   
318  DevilsFoot:466       kgc:subject   
434  DevilsFoot:487       kgc:subject   
42   DevilsFoot:415         kgc:where   
245  DevilsFoot:451    kgc:infoSource   
412  DevilsFoot:482    kgc:infoSource   
436  DevilsFoot:487            kgc:on   
310  DevilsFoot:464          kgc:what   
153  DevilsFoot:436       kgc:subject   
62   DevilsFoot:419       kgc:subject   
126  DevilsFoot:430       kgc:subject   
268  DevilsFoot:456          kgc:what   
200  DevilsFoot:444       kgc:subject   
382  DevilsFoot:476          kgc:what   
417  DevilsFoot:483    kgc:infoSource   
383  DevilsFoot:476    kgc:infoSource   
40   DevilsFoot:415       kgc:subject   
192  DevilsFoot:442          kgc:whom   
169  DevilsFoot:438          kgc:whom   
314  DevilsFoot:465       kgc:subject   
431  DevilsFoot:486    kgc:infoSource   
167  DevilsFoot:438          kgc:whom   
350  DevilsFoot:472       kgc:subject   
132  DevilsFoot:431          kgc:what   
138  DevilsFoot:433       kgc:subject   
271  DevilsFoot:457       kgc:subject   
398  DevilsFoot:480       kgc:subject   
308  DevilsFoot:464       kgc:subject   
146  DevilsFoot:434          kgc:what   
396  DevilsFoot:479    kgc:infoSource   
250  DevilsFoot:452          kgc:what   
297  DevilsFoot:462       kgc:subject   
406  DevilsFoot:481          kgc:from   
121  DevilsFoot:429       kgc:subject   
442  DevilsFoot:489       kgc:subject   
328  DevilsFoot:468       kgc:subject   
197  DevilsFoot:443          kgc:what   
59   DevilsFoot:418          kgc:when   
450        <mask_e>       kgc:subject   
154  DevilsFoot:436       kgc:subject   
321  DevilsFoot:466    kgc:infoSource   
45   DevilsFoot:416       kgc:subject   
416  DevilsFoot:483          kgc:what   
145  DevilsFoot:434          kgc:what   
294  DevilsFoot:461          kgc:whom   
43   DevilsFoot:415    kgc:infoSource   
385  DevilsFoot:477       kgc:subject   
380  DevilsFoot:476       kgc:subject   
155  DevilsFoot:436       kgc:subject   
58   DevilsFoot:418          kgc:when   
128  DevilsFoot:430          kgc:what   
151  DevilsFoot:435         kgc:where 

index=445, triple=['DevilsFoot:489', 'kgc:where', 'DevilsFoot:garden_of_Cottage_of_Sterndale'], attention list


...

head          relation  \
408  DevilsFoot:482       kgc:subject   
55   DevilsFoot:418       kgc:subject   
403  DevilsFoot:481       kgc:subject   
271  DevilsFoot:457       kgc:subject   
429  DevilsFoot:486       kgc:subject   
42   DevilsFoot:415         kgc:where   
256  DevilsFoot:454       kgc:subject   
411  DevilsFoot:482            kgc:to   
275  DevilsFoot:458       kgc:subject   
434  DevilsFoot:487       kgc:subject   
438  DevilsFoot:488       kgc:subject   
252  DevilsFoot:453       kgc:subject   
149  DevilsFoot:435       kgc:subject   
436  DevilsFoot:487            kgc:on   
273  DevilsFoot:457    kgc:infoSource   
34   DevilsFoot:414       kgc:subject   
138  DevilsFoot:433       kgc:subject   
143  DevilsFoot:434       kgc:subject   
67   DevilsFoot:420       kgc:subject   
453        <mask_e>         kgc:where   
172  DevilsFoot:439       kgc:subject   
313  DevilsFoot:465       kgc:subject   
141  DevilsFoot:433    kgc:infoSource   
419  DevilsFoot:484       kgc:subject   
333  DevilsFoot:469       kgc:subject   
59   DevilsFoot:418          kgc:when   
242  DevilsFoot:451       kgc:subject   
424  DevilsFoot:485       kgc:subject   
58   DevilsFoot:418          kgc:when   
62   DevilsFoot:419       kgc:subject   
60   DevilsFoot:418          kgc:time   
414  DevilsFoot:483       kgc:subject   
244  DevilsFoot:451         kgc:where   
314  DevilsFoot:465       kgc:subject   
134  DevilsFoot:432       kgc:subject   
126  DevilsFoot:430       kgc:subject   
40   DevilsFoot:415       kgc:subject   
405  DevilsFoot:481    kgc:infoSource   
376  DevilsFoot:475       kgc:subject   
258  DevilsFoot:454            kgc:to   
117  DevilsFoot:428       kgc:subject   
394  DevilsFoot:479       kgc:subject   
440  DevilsFoot:488         kgc:where   
308  DevilsFoot:464       kgc:subject   
147  DevilsFoot:434    kgc:infoSource   
380  DevilsFoot:476       kgc:subject   
140  DevilsFoot:433         kgc:where   
269  DevilsFoot:456    kgc:infoSource   
410  DevilsFoot:482          kgc:what   
174  DevilsFoot:439            kgc:to   
254  DevilsFoot:453    kgc:infoSource   
136  DevilsFoot:432    kgc:infoSource   
421  DevilsFoot:484         kgc:where   
103  DevilsFoot:425       kgc:subject   
412  DevilsFoot:482    kgc:infoSource   
318  DevilsFoot:466       kgc:subject   
306  DevilsFoot:463    kgc:infoSource   
121  DevilsFoot:429       kgc:subject   
431  DevilsFoot:486    kgc:infoSource   
151  DevilsFoot:435         kgc:where   
45   DevilsFoot:416       kgc:subject   
311  DevilsFoot:464    kgc:infoSource   
153  DevilsFoot:436       kgc:subject   
270         <bos_e>           <bos_r>   
261  DevilsFoot:455       kgc:subject   
260         <bos_e>           <bos_r>   
255         <bos_e>           <bos_r>   
266  DevilsFoot:456       kgc:subject   
328  DevilsFoot:468       kgc:subject   
43   DevilsFoot:415    kgc:infoSource   
450        <mask_e>       kgc:subject   
312         <bos_e>           <bos_r>   
52   DevilsFoot:417          kgc:what   
53   DevilsFoot:417    kgc:infoSource   
248  DevilsFoot:452       kgc:subject   
279  DevilsFoot:458    kgc:infoSource   
274         <bos_e>           <bos_r>   
301         <bos_e>           <bos_r>   
307         <bos_e>           <bos_r>   
245  DevilsFoot:451    kgc:infoSource   
422  DevilsFoot:484    kgc:infoSource   
137         <bos_e>           <bos_r>   
176  DevilsFoot:439          kgc:when   
128  DevilsFoot:430          kgc:what   
296         <bos_e>           <bos_r>   
165  DevilsFoot:438       kgc:subject   
265         <bos_e>           <bos_r>   
327         <bos_e>           <bos_r>   
407         <bos_e>           <bos_r>   
317         <bos_e>           <bos_r>   
310  DevilsFoot:464          kgc:what   
241         <bos_e>           <bos_r>   
251         <bos_e>           <bos_r>   
437         <bos_e>           <bos_r>   
132  DevilsFoot:431          kgc:what   
291         <bos_e>           <bos_r>   
398  DevilsFoot:480       kgc:subject 

index=452, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
408  DevilsFoot:482       kgc:subject   
55   DevilsFoot:418       kgc:subject   
429  DevilsFoot:486       kgc:subject   
403  DevilsFoot:481       kgc:subject   
52   DevilsFoot:417          kgc:what   
275  DevilsFoot:458       kgc:subject   
410  DevilsFoot:482          kgc:what   
434  DevilsFoot:487       kgc:subject   
126  DevilsFoot:430       kgc:subject   
424  DevilsFoot:485       kgc:subject   
436  DevilsFoot:487            kgc:on   
256  DevilsFoot:454       kgc:subject   
438  DevilsFoot:488       kgc:subject   
42   DevilsFoot:415         kgc:where   
411  DevilsFoot:482            kgc:to   
149  DevilsFoot:435       kgc:subject   
419  DevilsFoot:484       kgc:subject   
34   DevilsFoot:414       kgc:subject   
394  DevilsFoot:479       kgc:subject   
376  DevilsFoot:475       kgc:subject   
252  DevilsFoot:453       kgc:subject   
333  DevilsFoot:469       kgc:subject   
62   DevilsFoot:419       kgc:subject   
67   DevilsFoot:420       kgc:subject   
117  DevilsFoot:428       kgc:subject   
431  DevilsFoot:486    kgc:infoSource   
414  DevilsFoot:483       kgc:subject   
271  DevilsFoot:457       kgc:subject   
40   DevilsFoot:415       kgc:subject   
121  DevilsFoot:429       kgc:subject   
128  DevilsFoot:430          kgc:what   
242  DevilsFoot:451       kgc:subject   
103  DevilsFoot:425       kgc:subject   
453        <mask_e>         kgc:where   
141  DevilsFoot:433    kgc:infoSource   
405  DevilsFoot:481    kgc:infoSource   
421  DevilsFoot:484         kgc:where   
45   DevilsFoot:416       kgc:subject   
380  DevilsFoot:476       kgc:subject   
172  DevilsFoot:439       kgc:subject   
254  DevilsFoot:453    kgc:infoSource   
412  DevilsFoot:482    kgc:infoSource   
143  DevilsFoot:434       kgc:subject   
50   DevilsFoot:417       kgc:subject   
28   DevilsFoot:413       kgc:subject   
53   DevilsFoot:417    kgc:infoSource   
273  DevilsFoot:457    kgc:infoSource   
138  DevilsFoot:433       kgc:subject   
93   DevilsFoot:423       kgc:subject   
398  DevilsFoot:480       kgc:subject   
318  DevilsFoot:466       kgc:subject   
180  DevilsFoot:440       kgc:subject   
427  DevilsFoot:485    kgc:infoSource   
134  DevilsFoot:432       kgc:subject   
422  DevilsFoot:484    kgc:infoSource   
60   DevilsFoot:418          kgc:time   
372  DevilsFoot:474       kgc:subject   
183  DevilsFoot:440    kgc:infoSource   
147  DevilsFoot:434    kgc:infoSource   
43   DevilsFoot:415    kgc:infoSource   
132  DevilsFoot:431          kgc:what   
382  DevilsFoot:476          kgc:what   
153  DevilsFoot:436       kgc:subject   
310  DevilsFoot:464          kgc:what   
136  DevilsFoot:432    kgc:infoSource   
435  DevilsFoot:487   kgc:hasProperty   
313  DevilsFoot:465       kgc:subject   
328  DevilsFoot:468       kgc:subject   
269  DevilsFoot:456    kgc:infoSource   
130  DevilsFoot:431       kgc:subject   
151  DevilsFoot:435         kgc:where   
64   DevilsFoot:419    kgc:infoSource   
167  DevilsFoot:438          kgc:whom   
189  DevilsFoot:442       kgc:subject   
175  DevilsFoot:439    kgc:infoSource   
440  DevilsFoot:488         kgc:where   
277  DevilsFoot:458          kgc:what   
47   DevilsFoot:416          kgc:whom   
174  DevilsFoot:439            kgc:to   
145  DevilsFoot:434          kgc:what   
385  DevilsFoot:477       kgc:subject   
297  DevilsFoot:462       kgc:subject   
450        <mask_e>       kgc:subject   
308  DevilsFoot:464       kgc:subject   
73   DevilsFoot:421       kgc:subject   
266  DevilsFoot:456       kgc:subject   
154  DevilsFoot:436       kgc:subject   
217  DevilsFoot:446          kgc:what   
299  DevilsFoot:462          kgc:what   
378  DevilsFoot:475    kgc:infoSource   
279  DevilsFoot:458    kgc:infoSource   
426  DevilsFoot:485          kgc:what   
258  DevilsFoot:454            kgc:to   
294  DevilsFoot:461          kgc:whom   
314  DevilsFoot:465       kgc:subject   
284  DevilsFoot:459           kgc:why   
113  DevilsFoot:427       kgc:subject 

index=453, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
408  DevilsFoot:482       kgc:subject   
55   DevilsFoot:418       kgc:subject   
429  DevilsFoot:486       kgc:subject   
438  DevilsFoot:488       kgc:subject   
149  DevilsFoot:435       kgc:subject   
403  DevilsFoot:481       kgc:subject   
252  DevilsFoot:453       kgc:subject   
256  DevilsFoot:454       kgc:subject   
242  DevilsFoot:451       kgc:subject   
434  DevilsFoot:487       kgc:subject   
42   DevilsFoot:415         kgc:where   
126  DevilsFoot:430       kgc:subject   
333  DevilsFoot:469       kgc:subject   
308  DevilsFoot:464       kgc:subject   
453        <mask_e>         kgc:where   
172  DevilsFoot:439       kgc:subject   
424  DevilsFoot:485       kgc:subject   
394  DevilsFoot:479       kgc:subject   
411  DevilsFoot:482            kgc:to   
271  DevilsFoot:457       kgc:subject   
275  DevilsFoot:458       kgc:subject   
436  DevilsFoot:487            kgc:on   
117  DevilsFoot:428       kgc:subject   
153  DevilsFoot:436       kgc:subject   
328  DevilsFoot:468       kgc:subject   
60   DevilsFoot:418          kgc:time   
121  DevilsFoot:429       kgc:subject   
67   DevilsFoot:420       kgc:subject   
380  DevilsFoot:476       kgc:subject   
405  DevilsFoot:481    kgc:infoSource   
40   DevilsFoot:415       kgc:subject   
419  DevilsFoot:484       kgc:subject   
138  DevilsFoot:433       kgc:subject   
59   DevilsFoot:418          kgc:when   
58   DevilsFoot:418          kgc:when   
34   DevilsFoot:414       kgc:subject   
431  DevilsFoot:486    kgc:infoSource   
62   DevilsFoot:419       kgc:subject   
440  DevilsFoot:488         kgc:where   
254  DevilsFoot:453    kgc:infoSource   
376  DevilsFoot:475       kgc:subject   
141  DevilsFoot:433    kgc:infoSource   
421  DevilsFoot:484         kgc:where   
302  DevilsFoot:463       kgc:subject   
244  DevilsFoot:451         kgc:where   
273  DevilsFoot:457    kgc:infoSource   
245  DevilsFoot:451    kgc:infoSource   
143  DevilsFoot:434       kgc:subject   
103  DevilsFoot:425       kgc:subject   
151  DevilsFoot:435         kgc:where   
176  DevilsFoot:439          kgc:when   
432  DevilsFoot:486          kgc:when   
134  DevilsFoot:432       kgc:subject   
53   DevilsFoot:417    kgc:infoSource   
45   DevilsFoot:416       kgc:subject   
140  DevilsFoot:433         kgc:where   
414  DevilsFoot:483       kgc:subject   
311  DevilsFoot:464    kgc:infoSource   
136  DevilsFoot:432    kgc:infoSource   
313  DevilsFoot:465       kgc:subject   
410  DevilsFoot:482          kgc:what   
93   DevilsFoot:423       kgc:subject   
154  DevilsFoot:436       kgc:subject   
57   DevilsFoot:418    kgc:infoSource   
258  DevilsFoot:454            kgc:to   
306  DevilsFoot:463    kgc:infoSource   
248  DevilsFoot:452       kgc:subject   
175  DevilsFoot:439    kgc:infoSource   
28   DevilsFoot:413       kgc:subject   
180  DevilsFoot:440       kgc:subject   
155  DevilsFoot:436       kgc:subject   
398  DevilsFoot:480       kgc:subject   
174  DevilsFoot:439            kgc:to   
165  DevilsFoot:438       kgc:subject   
412  DevilsFoot:482    kgc:infoSource   
147  DevilsFoot:434    kgc:infoSource   
43   DevilsFoot:415    kgc:infoSource   
385  DevilsFoot:477       kgc:subject   
50   DevilsFoot:417       kgc:subject   
372  DevilsFoot:474       kgc:subject   
200  DevilsFoot:444       kgc:subject   
427  DevilsFoot:485    kgc:infoSource   
269  DevilsFoot:456    kgc:infoSource   
130  DevilsFoot:431       kgc:subject   
350  DevilsFoot:472       kgc:subject   
237  DevilsFoot:450       kgc:subject   
183  DevilsFoot:440    kgc:infoSource   
168  DevilsFoot:438          kgc:whom   
318  DevilsFoot:466       kgc:subject   
261  DevilsFoot:455       kgc:subject   
422  DevilsFoot:484    kgc:infoSource   
383  DevilsFoot:476    kgc:infoSource   
177  DevilsFoot:439          kgc:when   
266  DevilsFoot:456       kgc:subject   
343  DevilsFoot:471       kgc:subject   
310  DevilsFoot:464          kgc:what   
331  DevilsFoot:468    kgc:infoSource 

### AbbeyGrange(僧坊荘園)
Who killed Lord Blackenstall? (criminal & explanation)
被害者: Sir_Eustace_Brackenstall
犯人: 
犯行動機:

In [20]:
def do_AbbeyGrange_pred():
    title = 'AbbeyGrange'
    victim_name = 'Sir_Eustace_Brackenstall'
    killer_name = 'Jack_Croker'
    last_index = 414
    story_len = 80

    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_AbbeyGrange_pred()
pass

2023-02-03 04:59:31 - INFO - 2806554648.py - 12 - The pred ranking about AbbeyGrange:Jack_Croker is 0


predicate                                        whom  \
0           word.predicate:meet                             AllTitle:Holmes   
1           word.predicate:want        AbbeyGrange:Sir_Eustace_Brackenstall   
2            word.predicate:cut                  ACaseOfIdentity:Sutherland   
3            word.predicate:try                     AbbeyGrange:Jack_Croker   
4     word.predicate:cannotFind               AbbeyGrange:Lady_Brackenstall   
5           word.predicate:love                          CrookedMan:Barclay   
6           word.predicate:find                          AbbeyGrange:police   
7            word.predicate:say             ResidentPatient:Percy_Trevelyan   
8        word.predicate:notKnow               AbbeyGrange:Thought_of_Holmes   
9            word.predicate:hit                        AbbeyGrange:Criminal   
10           word.predicate:die                        word.predicate:marry   
11  ResidentPatient:Blessington       AbbeyGrange:Burglary_team_of_Lewisham   
12          word.predicate:send                 ResidentPatient:Blessington   
13          word.predicate:give                         word.predicate:meet   
14       word.predicate:putInto                      ACaseOfIdentity:Hosmer   
15        word.predicate:attend                           DancingMen:Cubitt   
16           word.predicate:ask                         word.predicate:send   
17          word.predicate:call                             DevilsFoot:lamp   
18         word.predicate:shout                 AbbeyGrange:Stanley_Hopkins   
19          word.predicate:fall  AbbeyGrange:Testimony_of_Lady_Brackenstall   

                                 subject  \
0                AbbeyGrange:Jack_Croker   
1                        AllTitle:Holmes   
2                  ACaseOfIdentity:Woman   
3                     CrookedMan:Barclay   
4          AbbeyGrange:Lady_Brackenstall   
5            ResidentPatient:Blessington   
6   AbbeyGrange:Sir_Eustace_Brackenstall   
7                        AllTitle:Watson   
8                    AbbeyGrange:Theresa   
9                      DancingMen:Cubitt   
10       ResidentPatient:Percy_Trevelyan   
11                    AbbeyGrange:police   
12            ResidentPatient:Helper_boy   
13                  SpeckledBand:Roylott   
14                      DancingMen:Elsie   
15            ACaseOfIdentity:Sutherland   
16           SilverBlaze:Fitzroy_Simpson   
17                  AbbeyGrange:Criminal   
18             ACaseOfIdentity:Windibank   
19              SilverBlaze:John_Straker   

                                     why  \
0            ResidentPatient:Blessington   
1                AbbeyGrange:Jack_Croker   
2                    word.predicate:meet   
3               AbbeyGrange:cord_of_bell   
4                 DevilsFoot:living_room   
5                       CrookedMan:Henry   
6                 word.predicate:request   
7          CrookedMan:key_of_living_room   
8                     AbbeyGrange:police   
9   AbbeyGrange:Sir_Eustace_Brackenstall   
10            ACaseOfIdentity:Sutherland   
11      ResidentPatient:Examination_room   
12                ACaseOfIdentity:letter   
13                  word.predicate:shout   
14       ResidentPatient:Percy_Trevelyan   
15      ResidentPatient:Blessington_room   
16                   word.predicate:send   
17                      CrookedMan:Nancy   
18                  word.predicate:marry   
19        SpeckledBand:Roylott_s_bedroom   

                                    what                                 where  
0            ResidentPatient:Blessington              AbbeyGrange:cord_of_bell  
1   AbbeyGrange:Sir_Eustace_Brackenstall  AbbeyGrange:Sir_Eustace_Brackenstall  
2                AbbeyGrange:Jack_Croker               AbbeyGrange:dining_room  
3               AbbeyGrange:cord_of_bell        SpeckledBand:Roylott_s_bedroom  
4                      AbbeyGrange:truth               AbbeyGrange:Jack_Croker  
5                       Cr

index=416, triple=['AbbeyGrange:414', 'kgc:hasPredicate', 'word.predicate:cannotFind'], attention list


head          relation  \
415   AbbeyGrange:414       kgc:subject   
382   AbbeyGrange:407       kgc:subject   
386   AbbeyGrange:407    kgc:infoSource   
419          <mask_e>    kgc:infoSource   
299   AbbeyGrange:392       kgc:subject   
303  AbbeyGrange:392a       kgc:subject   
405   AbbeyGrange:411    kgc:infoSource   
402   AbbeyGrange:411       kgc:subject   
416   AbbeyGrange:414  kgc:hasPredicate   
422          <mask_e>       kgc:subject   
413   AbbeyGrange:413    kgc:infoSource   
155   AbbeyGrange:364          kgc:what   
380   AbbeyGrange:406    kgc:infoSource   
388   AbbeyGrange:408       kgc:subject   
359   AbbeyGrange:402    kgc:infoSource   
321   AbbeyGrange:395    kgc:infoSource   
347   AbbeyGrange:400       kgc:subject   
296   AbbeyGrange:391    kgc:infoSource   
325   AbbeyGrange:396    kgc:infoSource   
385   AbbeyGrange:407            kgc:to   
365   AbbeyGrange:403    kgc:infoSource   
383   AbbeyGrange:407  kgc:hasPredicate   
410   AbbeyGrange:413       kgc:subject   
323   AbbeyGrange:396       kgc:subject   
408   AbbeyGrange:412   kgc:hasProperty   
350   AbbeyGrange:400    kgc:infoSource   
320   AbbeyGrange:395   kgc:hasProperty   
407   AbbeyGrange:412       kgc:subject   
317   AbbeyGrange:394    kgc:infoSource   
151   AbbeyGrange:363            kgc:on   
105   AbbeyGrange:354  kgc:hasPredicate   
117   AbbeyGrange:357  kgc:hasPredicate   
289   AbbeyGrange:390  kgc:hasPredicate   
314   AbbeyGrange:394       kgc:subject   
377   AbbeyGrange:406       kgc:subject   
195   AbbeyGrange:371          kgc:what   
374   AbbeyGrange:405    kgc:infoSource   
403   AbbeyGrange:411  kgc:hasPredicate   
133   AbbeyGrange:360       kgc:subject   
345  AbbeyGrange:399a    kgc:infoSource   
148   AbbeyGrange:363       kgc:subject   
290   AbbeyGrange:390    kgc:infoSource   
293   AbbeyGrange:391       kgc:subject   
361   AbbeyGrange:403       kgc:subject   
319   AbbeyGrange:395       kgc:subject   
301   AbbeyGrange:392          kgc:what   
263   AbbeyGrange:385       kgc:subject   
153   AbbeyGrange:364       kgc:subject   
224   AbbeyGrange:377       kgc:subject   
252   AbbeyGrange:382         kgc:where   
237   AbbeyGrange:379         kgc:where   
417   AbbeyGrange:414          kgc:what   
423          <mask_e>           kgc:why   
424          <mask_e>          kgc:what   
266   AbbeyGrange:385    kgc:infoSource   
327   AbbeyGrange:397       kgc:subject   
248   AbbeyGrange:381    kgc:infoSource   
342  AbbeyGrange:399a       kgc:subject   
288   AbbeyGrange:390       kgc:subject   
355   AbbeyGrange:401    kgc:infoSource   
123   AbbeyGrange:358  kgc:hasPredicate   
247   AbbeyGrange:381          kgc:what   
389   AbbeyGrange:408  kgc:hasPredicate   
393   AbbeyGrange:409       kgc:subject   
264   AbbeyGrange:385  kgc:hasPredicate   
335   AbbeyGrange:398    kgc:infoSource   
300   AbbeyGrange:392  kgc:hasPredicate   
218   AbbeyGrange:376  kgc:hasPredicate   
158   AbbeyGrange:365       kgc:subject   
352   AbbeyGrange:401       kgc:subject   
330   AbbeyGrange:397    kgc:infoSource   
250   AbbeyGrange:382       kgc:subject   
235   AbbeyGrange:379  kgc:hasPredicate   
332   AbbeyGrange:398       kgc:subject   
358   AbbeyGrange:402   kgc:hasProperty   
324   AbbeyGrange:396   kgc:hasProperty   
282   AbbeyGrange:388    kgc:infoSource   
225   AbbeyGrange:377  kgc:hasPredicate   
279   AbbeyGrange:388       kgc:subject   
246   AbbeyGrange:381  kgc:hasPredicate   
412   AbbeyGrange:413          kgc:what   
340   AbbeyGrange:399    kgc:infoSource   
316   AbbeyGrange:394          kgc:what   
284   AbbeyGrange:389       kgc:subject   
304  AbbeyGrange:392a  kgc:hasPredicate   
367   AbbeyGrange:404       kgc:subject   
245   AbbeyGrange:381       kgc:subject   
95    AbbeyGrange:352  kgc:hasPredicate   
310   AbbeyGrange:393    kgc:infoSource   
253   AbbeyGrange:382    kgc:infoSource   
223   AbbeyGrange:377       kgc:subject   
200   AbbeyGrange:372          kgc:what   
217   AbbeyGrange:

index=417, triple=['AbbeyGrange:414', 'kgc:what', 'AbbeyGrange:False_charge_person'], attention list


...

head          relation  \
402   AbbeyGrange:411       kgc:subject   
384   AbbeyGrange:407          kgc:what   
299   AbbeyGrange:392       kgc:subject   
410   AbbeyGrange:413       kgc:subject   
405   AbbeyGrange:411    kgc:infoSource   
361   AbbeyGrange:403       kgc:subject   
374   AbbeyGrange:405    kgc:infoSource   
359   AbbeyGrange:402    kgc:infoSource   
133   AbbeyGrange:360       kgc:subject   
385   AbbeyGrange:407            kgc:to   
342  AbbeyGrange:399a       kgc:subject   
422          <mask_e>       kgc:subject   
148   AbbeyGrange:363       kgc:subject   
415   AbbeyGrange:414       kgc:subject   
424          <mask_e>          kgc:what   
363   AbbeyGrange:403          kgc:what   
399   AbbeyGrange:410          kgc:what   
382   AbbeyGrange:407       kgc:subject   
314   AbbeyGrange:394       kgc:subject   
404   AbbeyGrange:411          kgc:what   
195   AbbeyGrange:371          kgc:what   
3     AbbeyGrange:335          kgc:what   
386   AbbeyGrange:407    kgc:infoSource   
407   AbbeyGrange:412       kgc:subject   
393   AbbeyGrange:409       kgc:subject   
155   AbbeyGrange:364          kgc:what   
344  AbbeyGrange:399a          kgc:what   
365   AbbeyGrange:403    kgc:infoSource   
412   AbbeyGrange:413          kgc:what   
301   AbbeyGrange:392          kgc:what   
364   AbbeyGrange:403          kgc:whom   
357   AbbeyGrange:402       kgc:subject   
293   AbbeyGrange:391       kgc:subject   
303  AbbeyGrange:392a       kgc:subject   
224   AbbeyGrange:377       kgc:subject   
372   AbbeyGrange:405       kgc:subject   
413   AbbeyGrange:413    kgc:infoSource   
425          <mask_e>         kgc:where   
151   AbbeyGrange:363            kgc:on   
265   AbbeyGrange:385          kgc:what   
423          <mask_e>           kgc:why   
367   AbbeyGrange:404       kgc:subject   
316   AbbeyGrange:394          kgc:what   
352   AbbeyGrange:401       kgc:subject   
355   AbbeyGrange:401    kgc:infoSource   
358   AbbeyGrange:402   kgc:hasProperty   
223   AbbeyGrange:377       kgc:subject   
226   AbbeyGrange:377            kgc:to   
408   AbbeyGrange:412   kgc:hasProperty   
284   AbbeyGrange:389       kgc:subject   
379   AbbeyGrange:406          kgc:what   
307   AbbeyGrange:393       kgc:subject   
110   AbbeyGrange:355    kgc:infoSource   
128   AbbeyGrange:359       kgc:subject   
219   AbbeyGrange:376          kgc:what   
158   AbbeyGrange:365       kgc:subject   
106   AbbeyGrange:354          kgc:what   
200   AbbeyGrange:372          kgc:what   
377   AbbeyGrange:406       kgc:subject   
321   AbbeyGrange:395    kgc:infoSource   
345  AbbeyGrange:399a    kgc:infoSource   
274   AbbeyGrange:387       kgc:subject   
153   AbbeyGrange:364       kgc:subject   
250   AbbeyGrange:382       kgc:subject   
165   AbbeyGrange:366          kgc:what   
114   AbbeyGrange:356    kgc:infoSource   
143   AbbeyGrange:362       kgc:subject   
252   AbbeyGrange:382         kgc:where   
138   AbbeyGrange:361       kgc:subject   
295   AbbeyGrange:391          kgc:what   
69    AbbeyGrange:347       kgc:subject   
112   AbbeyGrange:356       kgc:subject   
118   AbbeyGrange:357          kgc:what   
247   AbbeyGrange:381          kgc:what   
273   AbbeyGrange:387       kgc:subject   
417   AbbeyGrange:414          kgc:what   
354   AbbeyGrange:401          kgc:what   
116   AbbeyGrange:357       kgc:subject   
380   AbbeyGrange:406    kgc:infoSource   
319   AbbeyGrange:395       kgc:subject   
296   AbbeyGrange:391    kgc:infoSource   
64    AbbeyGrange:346       kgc:subject   
124   AbbeyGrange:358          kgc:what   
394   AbbeyGrange:409   kgc:hasProperty   
122   AbbeyGrange:358       kgc:subject   
369   AbbeyGrange:404          kgc:whom   
193   AbbeyGrange:371       kgc:subject   
400   AbbeyGrange:410    kgc:infoSource   
119   AbbeyGrange:357         kgc:where   
340   AbbeyGrange:399    kgc:infoSource   
421          <mask_e>          kgc:whom   
1     AbbeyGrange:335       kgc:subject   
419          <mask

index=424, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
299   AbbeyGrange:392       kgc:subject   
359   AbbeyGrange:402    kgc:infoSource   
386   AbbeyGrange:407    kgc:infoSource   
402   AbbeyGrange:411       kgc:subject   
374   AbbeyGrange:405    kgc:infoSource   
384   AbbeyGrange:407          kgc:what   
342  AbbeyGrange:399a       kgc:subject   
410   AbbeyGrange:413       kgc:subject   
314   AbbeyGrange:394       kgc:subject   
303  AbbeyGrange:392a       kgc:subject   
415   AbbeyGrange:414       kgc:subject   
382   AbbeyGrange:407       kgc:subject   
393   AbbeyGrange:409       kgc:subject   
352   AbbeyGrange:401       kgc:subject   
195   AbbeyGrange:371          kgc:what   
365   AbbeyGrange:403    kgc:infoSource   
405   AbbeyGrange:411    kgc:infoSource   
133   AbbeyGrange:360       kgc:subject   
422          <mask_e>       kgc:subject   
361   AbbeyGrange:403       kgc:subject   
355   AbbeyGrange:401    kgc:infoSource   
155   AbbeyGrange:364          kgc:what   
293   AbbeyGrange:391       kgc:subject   
248   AbbeyGrange:381    kgc:infoSource   
301   AbbeyGrange:392          kgc:what   
372   AbbeyGrange:405       kgc:subject   
316   AbbeyGrange:394          kgc:what   
224   AbbeyGrange:377       kgc:subject   
404   AbbeyGrange:411          kgc:what   
245   AbbeyGrange:381       kgc:subject   
424          <mask_e>          kgc:what   
413   AbbeyGrange:413    kgc:infoSource   
223   AbbeyGrange:377       kgc:subject   
200   AbbeyGrange:372          kgc:what   
385   AbbeyGrange:407            kgc:to   
347   AbbeyGrange:400       kgc:subject   
148   AbbeyGrange:363       kgc:subject   
345  AbbeyGrange:399a    kgc:infoSource   
337   AbbeyGrange:399       kgc:subject   
284   AbbeyGrange:389       kgc:subject   
158   AbbeyGrange:365       kgc:subject   
106   AbbeyGrange:354          kgc:what   
367   AbbeyGrange:404       kgc:subject   
265   AbbeyGrange:385          kgc:what   
339   AbbeyGrange:399          kgc:what   
350   AbbeyGrange:400    kgc:infoSource   
380   AbbeyGrange:406    kgc:infoSource   
250   AbbeyGrange:382       kgc:subject   
118   AbbeyGrange:357          kgc:what   
419          <mask_e>    kgc:infoSource   
307   AbbeyGrange:393       kgc:subject   
217   AbbeyGrange:376       kgc:subject   
319   AbbeyGrange:395       kgc:subject   
247   AbbeyGrange:381          kgc:what   
364   AbbeyGrange:403          kgc:whom   
340   AbbeyGrange:399    kgc:infoSource   
193   AbbeyGrange:371       kgc:subject   
153   AbbeyGrange:364       kgc:subject   
412   AbbeyGrange:413          kgc:what   
363   AbbeyGrange:403          kgc:what   
407   AbbeyGrange:412       kgc:subject   
357   AbbeyGrange:402       kgc:subject   
104   AbbeyGrange:354       kgc:subject   
399   AbbeyGrange:410          kgc:what   
417   AbbeyGrange:414          kgc:what   
296   AbbeyGrange:391    kgc:infoSource   
3     AbbeyGrange:335          kgc:what   
116   AbbeyGrange:357       kgc:subject   
128   AbbeyGrange:359       kgc:subject   
335   AbbeyGrange:398    kgc:infoSource   
358   AbbeyGrange:402   kgc:hasProperty   
219   AbbeyGrange:376          kgc:what   
151   AbbeyGrange:363            kgc:on   
274   AbbeyGrange:387       kgc:subject   
388   AbbeyGrange:408       kgc:subject   
344  AbbeyGrange:399a          kgc:what   
266   AbbeyGrange:385    kgc:infoSource   
377   AbbeyGrange:406       kgc:subject   
408   AbbeyGrange:412   kgc:hasProperty   
334   AbbeyGrange:398          kgc:what   
263   AbbeyGrange:385       kgc:subject   
400   AbbeyGrange:410    kgc:infoSource   
165   AbbeyGrange:366          kgc:what   
226   AbbeyGrange:377            kgc:to   
45    AbbeyGrange:343       kgc:subject   
108   AbbeyGrange:355       kgc:subject   
163   AbbeyGrange:366       kgc:subject   
255   AbbeyGrange:383       kgc:subject   
92    AbbeyGrange:351    kgc:infoSource   
187   AbbeyGrange:370       kgc:subject   
40    AbbeyGrange:342       kgc:subject   
124   AbbeyGrange:358          kgc:what   
112   AbbeyGrange:

index=425, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
299   AbbeyGrange:392       kgc:subject   
133   AbbeyGrange:360       kgc:subject   
402   AbbeyGrange:411       kgc:subject   
410   AbbeyGrange:413       kgc:subject   
359   AbbeyGrange:402    kgc:infoSource   
314   AbbeyGrange:394       kgc:subject   
384   AbbeyGrange:407          kgc:what   
361   AbbeyGrange:403       kgc:subject   
404   AbbeyGrange:411          kgc:what   
374   AbbeyGrange:405    kgc:infoSource   
415   AbbeyGrange:414       kgc:subject   
365   AbbeyGrange:403    kgc:infoSource   
303  AbbeyGrange:392a       kgc:subject   
158   AbbeyGrange:365       kgc:subject   
382   AbbeyGrange:407       kgc:subject   
405   AbbeyGrange:411    kgc:infoSource   
364   AbbeyGrange:403          kgc:whom   
293   AbbeyGrange:391       kgc:subject   
342  AbbeyGrange:399a       kgc:subject   
372   AbbeyGrange:405       kgc:subject   
363   AbbeyGrange:403          kgc:what   
153   AbbeyGrange:364       kgc:subject   
386   AbbeyGrange:407    kgc:infoSource   
224   AbbeyGrange:377       kgc:subject   
45    AbbeyGrange:343       kgc:subject   
193   AbbeyGrange:371       kgc:subject   
187   AbbeyGrange:370       kgc:subject   
284   AbbeyGrange:389       kgc:subject   
155   AbbeyGrange:364          kgc:what   
422          <mask_e>       kgc:subject   
248   AbbeyGrange:381    kgc:infoSource   
250   AbbeyGrange:382       kgc:subject   
3     AbbeyGrange:335          kgc:what   
116   AbbeyGrange:357       kgc:subject   
385   AbbeyGrange:407            kgc:to   
413   AbbeyGrange:413    kgc:infoSource   
34    AbbeyGrange:341       kgc:subject   
148   AbbeyGrange:363       kgc:subject   
245   AbbeyGrange:381       kgc:subject   
352   AbbeyGrange:401       kgc:subject   
112   AbbeyGrange:356       kgc:subject   
424          <mask_e>          kgc:what   
399   AbbeyGrange:410          kgc:what   
393   AbbeyGrange:409       kgc:subject   
316   AbbeyGrange:394          kgc:what   
1     AbbeyGrange:335       kgc:subject   
407   AbbeyGrange:412       kgc:subject   
247   AbbeyGrange:381          kgc:what   
122   AbbeyGrange:358       kgc:subject   
163   AbbeyGrange:366       kgc:subject   
106   AbbeyGrange:354          kgc:what   
425          <mask_e>         kgc:where   
174   AbbeyGrange:368       kgc:subject   
367   AbbeyGrange:404       kgc:subject   
296   AbbeyGrange:391    kgc:infoSource   
104   AbbeyGrange:354       kgc:subject   
307   AbbeyGrange:393       kgc:subject   
40    AbbeyGrange:342       kgc:subject   
138   AbbeyGrange:361       kgc:subject   
195   AbbeyGrange:371          kgc:what   
181   AbbeyGrange:369       kgc:subject   
108   AbbeyGrange:355       kgc:subject   
198   AbbeyGrange:372       kgc:subject   
357   AbbeyGrange:402       kgc:subject   
355   AbbeyGrange:401    kgc:infoSource   
274   AbbeyGrange:387       kgc:subject   
57    AbbeyGrange:345       kgc:subject   
156   AbbeyGrange:364    kgc:infoSource   
110   AbbeyGrange:355    kgc:infoSource   
412   AbbeyGrange:413          kgc:what   
189   AbbeyGrange:370          kgc:what   
151   AbbeyGrange:363            kgc:on   
118   AbbeyGrange:357          kgc:what   
64    AbbeyGrange:346       kgc:subject   
99    AbbeyGrange:353       kgc:subject   
217   AbbeyGrange:376       kgc:subject   
143   AbbeyGrange:362       kgc:subject   
223   AbbeyGrange:377       kgc:subject   
265   AbbeyGrange:385          kgc:what   
309   AbbeyGrange:393            kgc:to   
114   AbbeyGrange:356    kgc:infoSource   
50    AbbeyGrange:344       kgc:subject   
180   AbbeyGrange:369       kgc:subject   
150   AbbeyGrange:363    kgc:infoSource   
6     AbbeyGrange:336       kgc:subject   
128   AbbeyGrange:359       kgc:subject   
273   AbbeyGrange:387       kgc:subject   
169   AbbeyGrange:367       kgc:subject   
253   AbbeyGrange:382    kgc:infoSource   
380   AbbeyGrange:406    kgc:infoSource   
212   AbbeyGrange:375       kgc:subject   
377   AbbeyGrange:406       kgc:subject   
255   AbbeyGrange:

### 入院患者
Who killed Blessington? (criminal & explanation)
被害者: Blessington
犯人: 3人
犯行動機:

In [21]:
def do_ResidentPatient_pred():
    title = 'ResidentPatient'
    victim_name = 'Blessington'
    killer_name = ''
    last_index = 324
    story_len = 80

    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_ResidentPatient_pred()

2023-02-03 04:59:33 - INFO - 2806554648.py - 12 - The pred ranking about ResidentPatient: is -1


predicate                                whom  \
0       word.predicate:say         ResidentPatient:Blessington   
1      word.predicate:open     ResidentPatient:Percy_Trevelyan   
2      word.predicate:have                     AllTitle:Holmes   
3       word.predicate:sit                    CrookedMan:Nancy   
4      word.predicate:find                     AllTitle:Watson   
5       word.predicate:try         ResidentPatient:Elderly_man   
6      word.predicate:walk                   DancingMen:Cubitt   
7       word.predicate:die            SilverBlaze:John_Straker   
8     word.predicate:visit            SilverBlaze:Silver_Blaze   
9      word.predicate:want                    CrookedMan:Henry   
10  word.predicate:receive           ResidentPatient:Young_man   
11   word.predicate:notice    ResidentPatient:Blessington_room   
12  ACaseOfIdentity:Hosmer                 CrookedMan:Morrison   
13     word.predicate:meet                  CrookedMan:Barclay   
14    word.predicate:upset                    CrookedMan:beast   
15  word.predicate:notKnow              ACaseOfIdentity:Hosmer   
16    word.predicate:marry                  SilverBlaze:police   
17    word.predicate:exist  ResidentPatient:Brook_Street_house   
18    word.predicate:think          ACaseOfIdentity:Sutherland   
19  word.predicate:examine                 word.predicate:know   

                            subject  \
0       ResidentPatient:Blessington   
1                   AllTitle:Holmes   
2   ResidentPatient:Percy_Trevelyan   
3                   AllTitle:Watson   
4          SilverBlaze:Silver_Blaze   
5                 DancingMen:Cubitt   
6                  CrookedMan:Henry   
7               CrookedMan:Morrison   
8          SilverBlaze:John_Straker   
9                  CrookedMan:Nancy   
10      ResidentPatient:Elderly_man   
11        ResidentPatient:Young_man   
12       ResidentPatient:Helper_boy   
13          AbbeyGrange:Jack_Croker   
14              DevilsFoot:Mortimer   
15               word.predicate:ask   
16                 CrookedMan:beast   
17               CrookedMan:Barclay   
18            DancingMen:Abe_Slaney   
19               SilverBlaze:police   

                                           why  \
0                  ResidentPatient:Blessington   
1             ResidentPatient:Blessington_room   
2                           SilverBlaze:police   
3                     SilverBlaze:Silver_Blaze   
4                          word.predicate:know   
5           ResidentPatient:Brook_Street_house   
6                       ACaseOfIdentity:Hosmer   
7                             CrookedMan:Henry   
8   SilverBlaze:Mapleton_riding_ground_stables   
9                                      <bos_e>   
10                          CrookedMan:Rasheen   
11                        word.predicate:faint   
12                         word.predicate:want   
13                          word.predicate:ask   
14                 ResidentPatient:Elderly_man   
15                     AbbeyGrange:Jack_Croker   
16                      ACaseOfIdentity:letter   
17                    CrookedMan:Hudson_street   
18                 SilverBlaze:Wessex_Cup_game   
19                      DevilsFoot:living_room   

                                               what  \
0                       ResidentPatient:Blessington   
1                          SilverBlaze:Silver_Blaze   
2                                  CrookedMan:Henry   
3                                   AllTitle:Holmes   
4                                   AllTitle:Watson   
5                     SilverBlaze:Inspector_Gregory   
6                                 DancingMen:Cubitt   
7                       ResidentPatient:Elderly_man   
8                                word.predicate:ask   
9                                  CrookedMan:Nancy   
10                               SilverBlaze:police   
11                           word.predicate:suspect   
12                           DevilsFoot:livi

index=411, triple=['ResidentPatient:324', 'kgc:hasProperty', 'word.predicate:want'], attention list


head          relation  \
410   ResidentPatient:324       kgc:subject   
411   ResidentPatient:324   kgc:hasProperty   
406   ResidentPatient:323       kgc:subject   
412   ResidentPatient:324          kgc:what   
358   ResidentPatient:313       kgc:subject   
408   ResidentPatient:323          kgc:what   
407   ResidentPatient:323   kgc:hasProperty   
414              <mask_e>    kgc:infoSource   
174   ResidentPatient:278       kgc:subject   
354   ResidentPatient:312       kgc:subject   
83    ResidentPatient:263   kgc:hasProperty   
383   ResidentPatient:319       kgc:subject   
384   ResidentPatient:319       kgc:subject   
402   ResidentPatient:322       kgc:subject   
207   ResidentPatient:285       kgc:subject   
213   ResidentPatient:286       kgc:subject   
215   ResidentPatient:286       kgc:subject   
385   ResidentPatient:319       kgc:subject   
214   ResidentPatient:286       kgc:subject   
145   ResidentPatient:272       kgc:subject   
380   ResidentPatient:318       kgc:subject   
202   ResidentPatient:283    kgc:infoSource   
330   ResidentPatient:307   kgc:hasProperty   
381   ResidentPatient:318   kgc:hasProperty   
361   ResidentPatient:314       kgc:subject   
254  ResidentPatient:293a       kgc:subject   
355   ResidentPatient:312   kgc:hasProperty   
84    ResidentPatient:263          kgc:what   
86    ResidentPatient:264       kgc:subject   
318   ResidentPatient:305       kgc:subject   
219   ResidentPatient:287       kgc:subject   
205   ResidentPatient:284   kgc:hasProperty   
204   ResidentPatient:284       kgc:subject   
364   ResidentPatient:315       kgc:subject   
416              <mask_e>          kgc:whom   
404   ResidentPatient:322          kgc:what   
315   ResidentPatient:304       kgc:subject   
82    ResidentPatient:263       kgc:subject   
356   ResidentPatient:312          kgc:what   
379   ResidentPatient:318       kgc:subject   
146   ResidentPatient:272   kgc:hasProperty   
252  ResidentPatient:293a       kgc:subject   
351   ResidentPatient:311       kgc:subject   
258   ResidentPatient:294       kgc:subject   
208   ResidentPatient:285       kgc:subject   
209   ResidentPatient:285       kgc:subject   
368   ResidentPatient:316       kgc:subject   
253  ResidentPatient:293a       kgc:subject   
332   ResidentPatient:308       kgc:subject   
329   ResidentPatient:307       kgc:subject   
341  ResidentPatient:309a       kgc:subject   
417              <mask_e>       kgc:subject   
399   ResidentPatient:321   kgc:hasProperty   
220   ResidentPatient:287       kgc:subject   
256  ResidentPatient:293a          kgc:what   
172   ResidentPatient:277          kgc:what   
359   ResidentPatient:313   kgc:hasProperty   
177   ResidentPatient:279       kgc:subject   
313   ResidentPatient:304       kgc:subject   
325   ResidentPatient:306       kgc:subject   
178   ResidentPatient:279       kgc:subject   
87    ResidentPatient:264   kgc:hasProperty   
312   ResidentPatient:304       kgc:subject   
389  ResidentPatient:319a       kgc:subject   
398   ResidentPatient:321       kgc:subject   
321  ResidentPatient:305a       kgc:subject   
403   ResidentPatient:322   kgc:hasProperty   
221   ResidentPatient:287       kgc:subject   
217   ResidentPatient:286         kgc:where   
350   ResidentPatient:311       kgc:subject   
181   ResidentPatient:279          kgc:what   
170   ResidentPatient:277       kgc:subject   
378   ResidentPatient:318       kgc:subject   
149   ResidentPatient:273       kgc:subject   
198   ResidentPatient:282    kgc:infoSource   
229   ResidentPatient:289       kgc:subject   
147   ResidentPatient:272          kgc:what   
211   ResidentPatient:285          kgc:what   
246   ResidentPatient:293       kgc:subject   
334   ResidentPatient:308          kgc:whom   
225   ResidentPatient:288       kgc:subject   
259   ResidentPatient:294       kgc:subject   
400   ResidentPatient:321          kgc:when   
193   ResidentPatient:282       kgc:subject   
150   ResidentPatient:273 

index=412, triple=['ResidentPatient:324', 'kgc:what', 'ResidentPatient:324a'], attention list


...

index=419, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
417              <mask_e>       kgc:subject   
172   ResidentPatient:277          kgc:what   
101   ResidentPatient:267       kgc:subject   
312   ResidentPatient:304       kgc:subject   
412   ResidentPatient:324          kgc:what   
410   ResidentPatient:324       kgc:subject   
356   ResidentPatient:312          kgc:what   
63    ResidentPatient:259       kgc:subject   
332   ResidentPatient:308       kgc:subject   
408   ResidentPatient:323          kgc:what   
211   ResidentPatient:285          kgc:what   
77    ResidentPatient:262          kgc:what   
75    ResidentPatient:262          kgc:what   
79    ResidentPatient:262          kgc:what   
318   ResidentPatient:305       kgc:subject   
80    ResidentPatient:262          kgc:what   
65    ResidentPatient:259          kgc:what   
84    ResidentPatient:263          kgc:what   
174   ResidentPatient:278       kgc:subject   
315   ResidentPatient:304       kgc:subject   
313   ResidentPatient:304       kgc:subject   
70    ResidentPatient:261       kgc:subject   
418              <mask_e>           kgc:why   
361   ResidentPatient:314       kgc:subject   
76    ResidentPatient:262          kgc:what   
143   ResidentPatient:271          kgc:what   
82    ResidentPatient:263       kgc:subject   
416              <mask_e>          kgc:whom   
256  ResidentPatient:293a          kgc:what   
406   ResidentPatient:323       kgc:subject   
414              <mask_e>    kgc:infoSource   
402   ResidentPatient:322       kgc:subject   
27    ResidentPatient:252       kgc:subject   
364   ResidentPatient:315       kgc:subject   
114   ResidentPatient:270       kgc:subject   
147   ResidentPatient:272          kgc:what   
358   ResidentPatient:313       kgc:subject   
197   ResidentPatient:282          kgc:what   
67    ResidentPatient:260       kgc:subject   
181   ResidentPatient:279          kgc:what   
107   ResidentPatient:268       kgc:subject   
209   ResidentPatient:285       kgc:subject   
207   ResidentPatient:285       kgc:subject   
314   ResidentPatient:304       kgc:subject   
399   ResidentPatient:321   kgc:hasProperty   
153   ResidentPatient:273          kgc:what   
92    ResidentPatient:266       kgc:subject   
398   ResidentPatient:321       kgc:subject   
104   ResidentPatient:267          kgc:what   
329   ResidentPatient:307       kgc:subject   
419              <mask_e>          kgc:what   
16    ResidentPatient:249       kgc:subject   
99    ResidentPatient:266          kgc:time   
341  ResidentPatient:309a       kgc:subject   
178   ResidentPatient:279       kgc:subject   
420              <mask_e>         kgc:where   
254  ResidentPatient:293a       kgc:subject   
380   ResidentPatient:318       kgc:subject   
110   ResidentPatient:269       kgc:subject   
213   ResidentPatient:286       kgc:subject   
219   ResidentPatient:287       kgc:subject   
93    ResidentPatient:266       kgc:subject   
126   ResidentPatient:271          kgc:what   
78    ResidentPatient:262          kgc:what   
142   ResidentPatient:271          kgc:what   
208   ResidentPatient:285       kgc:subject   
94    ResidentPatient:266       kgc:subject   
321  ResidentPatient:305a       kgc:subject   
220   ResidentPatient:287       kgc:subject   
137   ResidentPatient:271          kgc:what   
404   ResidentPatient:322          kgc:what   
177   ResidentPatient:279       kgc:subject   
141   ResidentPatient:271          kgc:what   
194   ResidentPatient:282       kgc:subject   
195   ResidentPatient:282       kgc:subject   
24    ResidentPatient:251       kgc:subject   
221   ResidentPatient:287       kgc:subject   
136   ResidentPatient:271          kgc:what   
214   ResidentPatient:286       kgc:subject   
290   ResidentPatient:300       kgc:subject   
242   ResidentPatient:292       kgc:subject   
223   ResidentPatient:287          kgc:what   
258   ResidentPatient:294       kgc:subject   
73    ResidentPatient:262       kgc:subject   
351   ResidentPatient:311 

index=420, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
417              <mask_e>       kgc:subject   
414              <mask_e>    kgc:infoSource   
410   ResidentPatient:324       kgc:subject   
416              <mask_e>          kgc:whom   
398   ResidentPatient:321       kgc:subject   
358   ResidentPatient:313       kgc:subject   
418              <mask_e>           kgc:why   
313   ResidentPatient:304       kgc:subject   
312   ResidentPatient:304       kgc:subject   
332   ResidentPatient:308       kgc:subject   
101   ResidentPatient:267       kgc:subject   
174   ResidentPatient:278       kgc:subject   
315   ResidentPatient:304       kgc:subject   
219   ResidentPatient:287       kgc:subject   
420              <mask_e>         kgc:where   
402   ResidentPatient:322       kgc:subject   
207   ResidentPatient:285       kgc:subject   
215   ResidentPatient:286       kgc:subject   
202   ResidentPatient:283    kgc:infoSource   
214   ResidentPatient:286       kgc:subject   
220   ResidentPatient:287       kgc:subject   
314   ResidentPatient:304       kgc:subject   
380   ResidentPatient:318       kgc:subject   
16    ResidentPatient:249       kgc:subject   
209   ResidentPatient:285       kgc:subject   
63    ResidentPatient:259       kgc:subject   
361   ResidentPatient:314       kgc:subject   
213   ResidentPatient:286       kgc:subject   
208   ResidentPatient:285       kgc:subject   
99    ResidentPatient:266          kgc:time   
406   ResidentPatient:323       kgc:subject   
221   ResidentPatient:287       kgc:subject   
364   ResidentPatient:315       kgc:subject   
178   ResidentPatient:279       kgc:subject   
318   ResidentPatient:305       kgc:subject   
92    ResidentPatient:266       kgc:subject   
94    ResidentPatient:266       kgc:subject   
379   ResidentPatient:318       kgc:subject   
419              <mask_e>          kgc:what   
27    ResidentPatient:252       kgc:subject   
341  ResidentPatient:309a       kgc:subject   
150   ResidentPatient:273       kgc:subject   
351   ResidentPatient:311       kgc:subject   
368   ResidentPatient:316       kgc:subject   
395   ResidentPatient:320       kgc:subject   
383   ResidentPatient:319       kgc:subject   
344   ResidentPatient:310       kgc:subject   
82    ResidentPatient:263       kgc:subject   
354   ResidentPatient:312       kgc:subject   
151   ResidentPatient:273       kgc:subject   
378   ResidentPatient:318       kgc:subject   
93    ResidentPatient:266       kgc:subject   
334   ResidentPatient:308          kgc:whom   
204   ResidentPatient:284       kgc:subject   
217   ResidentPatient:286         kgc:where   
12    ResidentPatient:248       kgc:subject   
177   ResidentPatient:279       kgc:subject   
350   ResidentPatient:311       kgc:subject   
198   ResidentPatient:282    kgc:infoSource   
107   ResidentPatient:268       kgc:subject   
384   ResidentPatient:319       kgc:subject   
329   ResidentPatient:307       kgc:subject   
254  ResidentPatient:293a       kgc:subject   
67    ResidentPatient:260       kgc:subject   
233   ResidentPatient:290       kgc:subject   
229   ResidentPatient:289       kgc:subject   
385   ResidentPatient:319       kgc:subject   
194   ResidentPatient:282       kgc:subject   
188   ResidentPatient:281       kgc:subject   
89    ResidentPatient:265       kgc:subject   
114   ResidentPatient:270       kgc:subject   
70    ResidentPatient:261       kgc:subject   
193   ResidentPatient:282       kgc:subject   
183   ResidentPatient:280       kgc:subject   
170   ResidentPatient:277       kgc:subject   
372   ResidentPatient:317       kgc:subject   
290   ResidentPatient:300       kgc:subject   
110   ResidentPatient:269       kgc:subject   
300   ResidentPatient:302       kgc:subject   
389  ResidentPatient:319a       kgc:subject   
373   ResidentPatient:317       kgc:subject   
400   ResidentPatient:321          kgc:when   
195   ResidentPatient:282       kgc:subject   
399   ResidentPatient:321   kgc:hasProperty   
149   ResidentPatient:273 

(                                              predicate  \
 0                                    word.predicate:say   
 1                                   word.predicate:open   
 2                                   word.predicate:have   
 3                                    word.predicate:sit   
 4                                   word.predicate:find   
 ...                                                 ...   
 7844                                     DancingMen:156   
 7845                                    AbbeyGrange:395   
 7846                   SpeckledBand:as_hard_as_he_could   
 7847            SilverBlaze:bookmaker_of_small_gambling   
 7848  ResidentPatient:the_next_day_tens_of_around_fi...   
 
                                                    whom  \
 0                           ResidentPatient:Blessington   
 1                       ResidentPatient:Percy_Trevelyan   
 2                                       AllTitle:Holmes   
 3                                    

### 白銀
Who took out the White Silver Blaze? (criminal & explanation) 
被害者: Silver_Blaze
犯人: 
犯行動機:

In [22]:
victim = 'SilverBlaze:Silver_Blaze'
df_ranking_SilverBlaze, df_attension_SilverBlaze = make_ranking(
    'SilverBlaze:330', 'SilverBlaze:396', BRING, MASK_E, MASK_E, MASK_E, victim, MASK_E)

display(df_ranking_SilverBlaze.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_SilverBlaze)
for i in range(len_-20, len_):
    display(i, df_attension_SilverBlaze.iloc[i,:3].tolist())
    display(df_attension_SilverBlaze.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                              whom  \
0                  word.predicate:say          SilverBlaze:Silver_Blaze   
1                     AllTitle:Holmes          SilverBlaze:John_Straker   
2                  word.predicate:ask          SilverBlaze:Colonel_Ross   
3                word.predicate:think                   AllTitle:Holmes   
4                 word.predicate:have       SilverBlaze:Fitzroy_Simpson   
5                 word.predicate:know   ResidentPatient:Percy_Trevelyan   
6         ResidentPatient:Elderly_man     SilverBlaze:Inspector_Gregory   
7                 word.predicate:give       ResidentPatient:Blessington   
8       AbbeyGrange:Thought_of_Holmes                   AllTitle:Watson   
9         AbbeyGrange:Stanley_Hopkins                SilverBlaze:police   
10                 word.predicate:put  SilverBlaze:Wife_of_John_Straker   
11               AbbeyGrange:Criminal                word.predicate:ask   
12             ACaseOfIdentity:Hosmer  ResidentPatient:Lanner_Inspector   
13                word.predicate:find       ResidentPatient:Elderly_man   
14                word.predicate:open         ResidentPatient:Young_man   
15          word.predicate:cannotFind          SilverBlaze:Edith_Baxter   
16                word.predicate:walk                 DancingMen:Cubitt   
17  SilverBlaze:Night_of_the_incident               AbbeyGrange:Theresa   
18               word.predicate:visit                  CrookedMan:Nancy   
19                  word.predicate:go  ResidentPatient:Blessington_room   

                             subject  \
0           SilverBlaze:John_Straker   
1           SilverBlaze:Silver_Blaze   
2        SilverBlaze:Fitzroy_Simpson   
3                    AllTitle:Holmes   
4           SilverBlaze:Colonel_Ross   
5        ResidentPatient:Blessington   
6      SilverBlaze:Inspector_Gregory   
7                AbbeyGrange:Theresa   
8                  DancingMen:Cubitt   
9   SilverBlaze:Wife_of_John_Straker   
10           SilverBlaze:Brown_horse   
11                   AllTitle:Watson   
12          SilverBlaze:Edith_Baxter   
13   ResidentPatient:Percy_Trevelyan   
14  ResidentPatient:Lanner_Inspector   
15                word.predicate:ask   
16     AbbeyGrange:Lady_Brackenstall   
17           SilverBlaze:Silas_Brown   
18           AbbeyGrange:Jack_Croker   
19                SilverBlaze:police   

                                           why  \
0                     SilverBlaze:Silver_Blaze   
1   SilverBlaze:Mapleton_riding_ground_stables   
2                  ResidentPatient:Blessington   
3                        ACaseOfIdentity:Chair   
4                          word.predicate:know   
5        ResidentPatient:Wheel_of_a_large_rope   
6                     SilverBlaze:Colonel_Ross   
7                           word.predicate:ask   
8                      AbbeyGrange:Jack_Croker   
9           ResidentPatient:Brook_Street_house   
10                          SilverBlaze:police   
11                      DevilsFoot:living_room   
12                      SilverBlaze:Desborough   
13                       SilverBlaze:Wasteland   
14                      ACaseOfIdentity:letter   
15                         word.predicate:wear   
16            ResidentPatient:Lanner_Inspector   
17               CrookedMan:key_of_living_room   
18                      SilverBlaze:Ned_Hunter   
19                 ResidentPatient:Elderly_man   

                                     what                              where  
0                SilverBlaze:Silver_Blaze           SilverBlaze:Silver_Blaze  
1                SilverBlaze:John_Straker                            <bos_e>  
2                SilverBlaze:Colonel_Ross    ResidentPatient:Percy_Trevelyan  
3             ResidentPatient:Blessington                 SilverBlaze:stable  
4                 SilverBlaze:Brown_horse    SpeckledBand:mansion_of_Roylott  
5                      SilverBlaze:police                word.predicate:know  
6      

364

['SilverBlaze:394', 'kgc:hasPredicate', 'word.predicate:buy']

head         relation                           tail  \
367   SilverBlaze:395      kgc:subject       SilverBlaze:John_Straker   
363   SilverBlaze:394      kgc:subject       SilverBlaze:John_Straker   
359  SilverBlaze:393a      kgc:subject                AllTitle:Holmes   
365   SilverBlaze:394         kgc:what  SilverBlaze:Expensive_clothes   
361  SilverBlaze:393a         kgc:what                SilverBlaze:394   
377          <mask_e>   kgc:infoSource                AllTitle:Holmes   
372   SilverBlaze:396      kgc:subject       SilverBlaze:Colonel_Ross   
1     SilverBlaze:330      kgc:subject                AllTitle:Holmes   
4     SilverBlaze:330           kgc:to       SilverBlaze:Colonel_Ross   
76    SilverBlaze:345      kgc:subject                AllTitle:Holmes   
369   SilverBlaze:395         kgc:what               SilverBlaze:debt   
370   SilverBlaze:395          kgc:why                SilverBlaze:394   
348   SilverBlaze:391         kgc:what              SilverBlaze:cloak   
335   SilverBlaze:389      kgc:subject       SilverBlaze:Silver_Blaze   
240   SilverBlaze:371      kgc:subject       SilverBlaze:John_Straker   
86    SilverBlaze:346      kgc:subject        SilverBlaze:Brown_horse   
62   SilverBlaze:342a      kgc:subject        SilverBlaze:Brown_horse   
346   SilverBlaze:391      kgc:subject       SilverBlaze:John_Straker   
89    SilverBlaze:347      kgc:subject                AllTitle:Holmes   
87    SilverBlaze:346  kgc:hasProperty    word.predicate:Silver_Blaze   

     atten_from364  
367       0.015796  
363       0.015069  
359       0.010987  
365       0.010765  
361       0.010528  
377       0.010166  
372       0.010072  
1         0.010062  
4         0.009487  
76        0.008379  
369       0.007445  
370       0.007191  
348       0.007030  
335       0.006999  
240       0.006923  
86        0.006732  
62        0.006713  
346       0.006594  
89        0.006434  
87        0.006397

----------


...

----------


383

['<mask_e>', 'kgc:where', '<mask_e>']

head        relation  \
363   SilverBlaze:394     kgc:subject   
383          <mask_e>       kgc:where   
51    SilverBlaze:340          kgc:on   
377          <mask_e>  kgc:infoSource   
372   SilverBlaze:396     kgc:subject   
62   SilverBlaze:342a     kgc:subject   
59    SilverBlaze:342        kgc:what   
47    SilverBlaze:339        kgc:from   
367   SilverBlaze:395     kgc:subject   
57    SilverBlaze:342     kgc:subject   
330   SilverBlaze:388     kgc:subject   
346   SilverBlaze:391     kgc:subject   
319   SilverBlaze:386       kgc:where   
380          <mask_e>     kgc:subject   
381          <mask_e>         kgc:why   
351   SilverBlaze:392     kgc:subject   
43    SilverBlaze:338          kgc:on   
375   SilverBlaze:396          kgc:to   
382          <mask_e>        kgc:what   
335   SilverBlaze:389     kgc:subject   

                                         tail  atten_from383  
363                  SilverBlaze:John_Straker       0.015060  
383                                  <mask_e>       0.012080  
51                    SilverBlaze:Brown_horse       0.011848  
377                           AllTitle:Holmes       0.011825  
372                  SilverBlaze:Colonel_Ross       0.011437  
62                    SilverBlaze:Brown_horse       0.010490  
59                   SilverBlaze:Silver_Blaze       0.010403  
47     SilverBlaze:Weight_inspection_stations       0.009561  
367                  SilverBlaze:John_Straker       0.008932  
57                    SilverBlaze:Brown_horse       0.008891  
330                  SilverBlaze:John_Straker       0.008681  
346                  SilverBlaze:John_Straker       0.008649  
319             SilverBlaze:Dent_of_wasteland       0.008614  
380                                  <mask_e>       0.008608  
381                                  <mask_e>       0.008245  
351                  SilverBlaze:John_Straker       0.008120  
43   SilverBlaze:Competition_subscriber_table       0.008031  
375                           AllTitle:Holmes       0.007933  
382                  SilverBlaze:Silver_Blaze       0.007853  
335                  SilverBlaze:Silver_Blaze       0.007430

----------


### CrookedMan(背中の曲がった男):
Why did Barclay die?
被害者: Barclay
犯人:
犯行動機:

In [23]:
victim = 'CrookedMan:Barclay'
df_ranking_CrookedMan, df_attension_CrookedMan = make_ranking(
    f'CrookedMan:{373-80+1}', 'CrookedMan:373', DIE, MASK_E, victim, MASK_E, MASK_E, MASK_E)

display(df_ranking_CrookedMan.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_CrookedMan)
for i in range(len_-20, len_):
    display(i, df_attension_CrookedMan.iloc[i,:3].tolist())
    display(df_attension_CrookedMan.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                                  whom  \
0              word.predicate:say                       AllTitle:Holmes   
1              word.predicate:die                      DancingMen:Elsie   
2             word.predicate:know                      CrookedMan:Nancy   
3             word.predicate:have                     DancingMen:Cubitt   
4          ACaseOfIdentity:Hosmer            ACaseOfIdentity:Sutherland   
5            word.predicate:exist                    CrookedMan:Barclay   
6            AbbeyGrange:Criminal                       AllTitle:Watson   
7                 AllTitle:Holmes             ACaseOfIdentity:Windibank   
8             word.predicate:find                ACaseOfIdentity:Hosmer   
9            word.predicate:marry       ResidentPatient:Percy_Trevelyan   
10  AbbeyGrange:Thought_of_Holmes         AbbeyGrange:Thought_of_Holmes   
11          word.predicate:notice                   DevilsFoot:Mortimer   
12          word.predicate:escape             ResidentPatient:Young_man   
13            word.predicate:fall  AbbeyGrange:Sir_Eustace_Brackenstall   
14        word.predicate:notExist                  word.predicate:marry   
15           word.predicate:think                       CrookedMan:Jane   
16            word.predicate:wear                    SpeckledBand:Helen   
17           word.predicate:upset                ACaseOfIdentity:letter   
18              word.predicate:go           AbbeyGrange:Stanley_Hopkins   
19           word.predicate:visit                               <bos_e>   

                            subject                                 why  \
0                   AllTitle:Holmes    ResidentPatient:Examination_room   
1                CrookedMan:Barclay   SilverBlaze:Night_of_the_incident   
2                 DancingMen:Cubitt                  SpeckledBand:Helen   
3         ACaseOfIdentity:Windibank             AbbeyGrange:Jack_Croker   
4     AbbeyGrange:Thought_of_Holmes                     AllTitle:Holmes   
5   ResidentPatient:Percy_Trevelyan             word.predicate:notExist   
6          SilverBlaze:John_Straker              ACaseOfIdentity:letter   
7            ACaseOfIdentity:Hosmer    ResidentPatient:Blessington_room   
8        ACaseOfIdentity:Sutherland                 word.predicate:know   
9                  CrookedMan:Nancy  ResidentPatient:Brook_Street_house   
10      ResidentPatient:Blessington            CrookedMan:Hudson_street   
11      SilverBlaze:Fitzroy_Simpson              ACaseOfIdentity:Hosmer   
12                  AllTitle:Watson                  word.predicate:die   
13                 DancingMen:Elsie                  word.predicate:see   
14             word.predicate:marry            SilverBlaze:Silver_Blaze   
15        ResidentPatient:Young_man                AbbeyGrange:Criminal   
16              DevilsFoot:Mortimer          ResidentPatient:Helper_boy   
17        SilverBlaze:two_young_men                 ACaseOfIdentity:450   
18    AbbeyGrange:Lady_Brackenstall                    DancingMen:Elsie   
19     DateTime:1883-04-01T15:00:00                word.predicate:marry   

                                    what                            where  
0                        AllTitle:Holmes                  AllTitle:Holmes  
1                        DevilsFoot:lamp    AbbeyGrange:Thought_of_Holmes  
2   AbbeyGrange:Sir_Eustace_Brackenstall      AbbeyGrange:Stanley_Hopkins  
3             ACaseOfIdentity:Sutherland                  AllTitle:Watson  
4          AbbeyGrange:Thought_of_Holmes              word.predicate:know  
5                 ACaseOfIdentity:letter       SpeckledBand:1883-04-01T14  
6          CrookedMan:key_of_living_room           DevilsFoot:living_room  
7               SilverBlaze:Silver_Blaze  SpeckledBand:mansion_of_Roylott  
8                    DevilsFoot:Mortimer          SilverBlaze:Silas_Brown  
9               CrookedMan:Hudson_street               SpeckledBand:Helen  
10                    word.predicate

398

['CrookedMan:371', 'kgc:infoSource', 'AllTitle:Holmes']

head          relation                      tail  atten_from398
396  CrookedMan:371  kgc:hasPredicate        word.predicate:sin       0.032532
401  CrookedMan:372  kgc:hasPredicate      word.predicate:exist       0.014270
254  CrookedMan:339  kgc:hasPredicate     word.predicate:putOut       0.013793
301  CrookedMan:352       kgc:subject          CrookedMan:Teddy       0.011452
313  CrookedMan:355       kgc:subject          CrookedMan:Teddy       0.009391
398  CrookedMan:371    kgc:infoSource           AllTitle:Holmes       0.009301
228  CrookedMan:334  kgc:hasPredicate       word.predicate:drop       0.008615
308  CrookedMan:353       kgc:subject          CrookedMan:Teddy       0.008543
394  CrookedMan:371       kgc:subject         CrookedMan:Davide       0.007705
293  CrookedMan:350       kgc:subject          CrookedMan:Henry       0.007701
285  CrookedMan:348       kgc:subject          CrookedMan:Henry       0.007651
365  CrookedMan:366       kgc:subject        CrookedMan:Barclay       0.007422
258  CrookedMan:340       kgc:subject  CrookedMan:hair_of_beast       0.007420
192  CrookedMan:328       kgc:subject          CrookedMan:Henry       0.007046
390  CrookedMan:370       kgc:subject         CrookedMan:Davide       0.007045
392  CrookedMan:370    kgc:infoSource           AllTitle:Holmes       0.006748
406  CrookedMan:373  kgc:hasPredicate      word.predicate:exist       0.006698
69   CrookedMan:306       kgc:subject          CrookedMan:Henry       0.006697
177  CrookedMan:325  kgc:hasPredicate      word.predicate:think       0.006606
243  CrookedMan:337       kgc:subject          CrookedMan:Henry       0.006557

----------


...

----------


417

['<mask_e>', 'kgc:where', '<mask_e>']

head        relation  \
400  CrookedMan:372     kgc:subject   
411        <mask_e>  kgc:infoSource   
405  CrookedMan:373     kgc:subject   
413        <mask_e>        kgc:whom   
301  CrookedMan:352     kgc:subject   
308  CrookedMan:353     kgc:subject   
403  CrookedMan:372  kgc:infoSource   
402  CrookedMan:372       kgc:where   
388  CrookedMan:369  kgc:infoSource   
414        <mask_e>     kgc:subject   
385  CrookedMan:369     kgc:subject   
313  CrookedMan:355     kgc:subject   
409  CrookedMan:373  kgc:infoSource   
398  CrookedMan:371  kgc:infoSource   
407  CrookedMan:373        kgc:what   
390  CrookedMan:370     kgc:subject   
392  CrookedMan:370  kgc:infoSource   
326  CrookedMan:358     kgc:subject   
416        <mask_e>        kgc:what   
408  CrookedMan:373        kgc:what   

                                          tail  atten_from417  
400                   CrookedMan:sin_of_Davide       0.018800  
411                            AllTitle:Holmes       0.014219  
405  CrookedMan:episode_of_Uriah_and_Bathsheba       0.013215  
413                                   <mask_e>       0.011260  
301                           CrookedMan:Teddy       0.011200  
308                           CrookedMan:Teddy       0.010500  
403                            AllTitle:Holmes       0.010164  
402  CrookedMan:episode_of_Uriah_and_Bathsheba       0.009643  
388                            AllTitle:Holmes       0.009360  
414                         CrookedMan:Barclay       0.009305  
385                          CrookedMan:Davide       0.009263  
313                           CrookedMan:Teddy       0.009172  
409                            AllTitle:Holmes       0.008883  
398                            AllTitle:Holmes       0.008796  
407               CrookedMan:preface_of_Samuel       0.008793  
390                          CrookedMan:Davide       0.008781  
392                            AllTitle:Holmes       0.008558  
326                         CrookedMan:Barclay       0.008222  
416                                   <mask_e>       0.008086  
408            CrookedMan:postscript_of_Samuel       0.007984

----------


### 花嫁失踪事件（同一事件）
hozmaの失踪の名瀬を探る
被害者: ACaseOfIdentity:Hozma
犯人: 
犯行動機: 

In [24]:
victim = 'ACaseOfIdentity:Hosmer'
df_ranking_ACaseOfIdentity, df_attension_ACaseOfIdentity = make_ranking(
    'ACaseOfIdentity:510', 'ACaseOfIdentity:578', HIDE, victim, MASK_E, MASK_E, MASK_E, MASK_E)

display(df_ranking_ACaseOfIdentity.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_ACaseOfIdentity)
for i in range(len_-20, len_):
    display(i, df_attension_ACaseOfIdentity.iloc[i,:3].tolist())
    display(df_attension_ACaseOfIdentity.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")


predicate                                  whom  \
0            word.predicate:say            ACaseOfIdentity:Sutherland   
1           word.predicate:wear                       AllTitle:Holmes   
2           word.predicate:have                ACaseOfIdentity:Hosmer   
3        word.predicate:notKnow             ACaseOfIdentity:Windibank   
4          word.predicate:exist                      CrookedMan:Nancy   
5             word.predicate:go                    CrookedMan:Barclay   
6        ACaseOfIdentity:Hosmer          DateTime:1883-04-01T15:00:00   
7           word.predicate:open                     SilverBlaze:knife   
8           word.predicate:find               AbbeyGrange:Jack_Croker   
9           word.predicate:want                      CrookedMan:Henry   
10            DevilsFoot:George                     DancingMen:Cubitt   
11             CrookedMan:Nancy                ACaseOfIdentity:letter   
12       word.predicate:examine                    word.predicate:say   
13          word.predicate:know         AbbeyGrange:Thought_of_Holmes   
14   ACaseOfIdentity:Sutherland           AbbeyGrange:Stanley_Hopkins   
15          word.predicate:meet                   word.predicate:send   
16    word.predicate:cannotFind               word.predicate:notExist   
17           word.predicate:die                      DancingMen:Elsie   
18       word.predicate:receive  AbbeyGrange:Sir_Eustace_Brackenstall   
19  AbbeyGrange:Stanley_Hopkins                  AbbeyGrange:Criminal   

                                  subject                                why  \
0              ACaseOfIdentity:Sutherland                word.predicate:know   
1                         AllTitle:Holmes                   CrookedMan:Henry   
2               ACaseOfIdentity:Windibank             ACaseOfIdentity:Hosmer   
3                  ACaseOfIdentity:Hosmer            AbbeyGrange:Jack_Croker   
4            DateTime:1883-04-01T15:00:00              ACaseOfIdentity:Chair   
5           AbbeyGrange:Thought_of_Holmes                word.predicate:meet   
6                      CrookedMan:Barclay                word.predicate:want   
7                       DancingMen:Cubitt        AbbeyGrange:Stanley_Hopkins   
8             AbbeyGrange:Stanley_Hopkins         ACaseOfIdentity:Sutherland   
9                       SilverBlaze:knife            word.predicate:notExist   
10                       DancingMen:Elsie                word.predicate:give   
11                   ACaseOfIdentity:door        ResidentPatient:Elderly_man   
12                word.predicate:notExist        ResidentPatient:Blessington   
13                       CrookedMan:Nancy               word.predicate:visit   
14                AbbeyGrange:Jack_Croker  SilverBlaze:Night_of_the_incident   
15   AbbeyGrange:Sir_Eustace_Brackenstall                            <bos_e>   
16        ResidentPatient:Percy_Trevelyan             ACaseOfIdentity:letter   
17                   AbbeyGrange:Criminal                 SilverBlaze:police   
18                     word.predicate:say                    AllTitle:Holmes   
19  ACaseOfIdentity:Sutherland_s_thoughts                 AbbeyGrange:police   

                                    what                              where  
0                        AllTitle:Holmes                    AllTitle:Holmes  
1      ACaseOfIdentity:missing_of_Hosmer         ACaseOfIdentity:Sutherland  
2                 ACaseOfIdentity:others        AbbeyGrange:Stanley_Hopkins  
3                AbbeyGrange:Jack_Croker                   CrookedMan:Nancy  
4                 ACaseOfIdentity:letter           AbbeyGrange:cord_of_bell  
5                       CrookedMan:Henry  SilverBlaze:Night_of_the_incident  
6             ACaseOfIdentity:Sutherland                   CrookedMan:Henry  
7                 ACaseOfIdentity:Hosmer               ACaseOfIdentity:door  
8            AbbeyGrange:Stanley_Hopkins        ResidentPatient:Elderly_man  
9               word.predic

356

['ACaseOfIdentity:576', 'kgc:what', 'ACaseOfIdentity:577']

head        relation                                tail  \
79   ACaseOfIdentity:521        kgc:what                 ACaseOfIdentity:522   
73   ACaseOfIdentity:520        kgc:what          ACaseOfIdentity:Sutherland   
111  ACaseOfIdentity:528        kgc:what                 ACaseOfIdentity:529   
80   ACaseOfIdentity:521  kgc:infoSource                     AllTitle:Holmes   
214  ACaseOfIdentity:552        kgc:what                 ACaseOfIdentity:sin   
165  ACaseOfIdentity:541        kgc:what                 ACaseOfIdentity:543   
351  ACaseOfIdentity:575        kgc:what              ACaseOfIdentity:Hosmer   
359  ACaseOfIdentity:577     kgc:subject  ACaseOfIdentity:Personal_statement   
132  ACaseOfIdentity:532        kgc:what              ACaseOfIdentity:others   
68   ACaseOfIdentity:519          kgc:to              ACaseOfIdentity:others   
178  ACaseOfIdentity:543        kgc:what                 ACaseOfIdentity:law   
169  ACaseOfIdentity:541        kgc:what                 ACaseOfIdentity:547   
347  ACaseOfIdentity:574  kgc:infoSource                     AllTitle:Holmes   
167  ACaseOfIdentity:541        kgc:what                 ACaseOfIdentity:545   
302  ACaseOfIdentity:565        kgc:what           ACaseOfIdentity:signature   
77   ACaseOfIdentity:521     kgc:subject           ACaseOfIdentity:Windibank   
286  ACaseOfIdentity:562        kgc:what               ACaseOfIdentity:money   
168  ACaseOfIdentity:541        kgc:what                 ACaseOfIdentity:546   
354  ACaseOfIdentity:576     kgc:subject             ACaseOfIdentity:company   
352  ACaseOfIdentity:575  kgc:infoSource                     AllTitle:Holmes   

     atten_from356  
79        0.031289  
73        0.013621  
111       0.012739  
80        0.010170  
214       0.010105  
165       0.010006  
351       0.008774  
359       0.008632  
132       0.008506  
68        0.008271  
178       0.008139  
169       0.008137  
347       0.007841  
167       0.007818  
302       0.007595  
77        0.007581  
286       0.007339  
168       0.007303  
354       0.007077  
352       0.006997

----------


...

----------


375

['<mask_e>', 'kgc:where', '<mask_e>']

head     relation                                    tail  \
79   ACaseOfIdentity:521     kgc:what                     ACaseOfIdentity:522   
290  ACaseOfIdentity:563  kgc:subject                  ACaseOfIdentity:Hosmer   
143  ACaseOfIdentity:535       kgc:to                  ACaseOfIdentity:Church   
289  ACaseOfIdentity:563  kgc:subject               ACaseOfIdentity:Windibank   
73   ACaseOfIdentity:520     kgc:what              ACaseOfIdentity:Sutherland   
68   ACaseOfIdentity:519       kgc:to                  ACaseOfIdentity:others   
218  ACaseOfIdentity:553  kgc:subject    ACaseOfIdentity:friend_of_Sutherland   
217  ACaseOfIdentity:553  kgc:subject   ACaseOfIdentity:brother_of_Sutherland   
142  ACaseOfIdentity:535     kgc:what              ACaseOfIdentity:Sutherland   
75   ACaseOfIdentity:520     kgc:when                 ACaseOfIdentity:Forever   
305  ACaseOfIdentity:566  kgc:subject              ACaseOfIdentity:Sutherland   
111  ACaseOfIdentity:528     kgc:what                     ACaseOfIdentity:529   
185  ACaseOfIdentity:544     kgc:when                     ACaseOfIdentity:547   
349  ACaseOfIdentity:575  kgc:subject         ACaseOfIdentity:feature_of_type   
286  ACaseOfIdentity:562     kgc:what                   ACaseOfIdentity:money   
214  ACaseOfIdentity:552     kgc:what                     ACaseOfIdentity:sin   
372             <mask_e>  kgc:subject                                <mask_e>   
66   ACaseOfIdentity:519  kgc:subject      ACaseOfIdentity:love_of_Sutherland   
361  ACaseOfIdentity:577     kgc:what               ACaseOfIdentity:Windibank   
117  ACaseOfIdentity:529     kgc:when  ACaseOfIdentity:morning_of_wedding_day   

     atten_from375  
79        0.019637  
290       0.013448  
143       0.012617  
289       0.012423  
73        0.011577  
68        0.011479  
218       0.010134  
217       0.009968  
142       0.009547  
75        0.008819  
305       0.008184  
111       0.008150  
185       0.008104  
349       0.008029  
286       0.007697  
214       0.007373  
372       0.007317  
66        0.007244  
361       0.007178  
117       0.007056

----------
